# Transformação de Dados

Nos notebooks anteriores, aprendemos a usar marcas e codificações visuais para representar registros individuais de dados. Aqui, exploraremos métodos para *transformar* dados, incluindo o uso de agregações para resumir múltiplos registros. A transformação de dados é uma parte essencial da visualização: escolher quais variáveis exibir e seu nível de detalhamento é tão importante quanto escolher codificações visuais apropriadas. Afinal, não importa quão bem escolhidas sejam suas codificações visuais se você estiver mostrando as informações erradas!

À medida que você avança neste módulo, recomendamos que abra a [documentação de Transformações de Dados do Altair](https://altair-viz.github.io/user_guide/transform/index.html) em outra aba. Ela será um recurso útil caso você queira mais detalhes ou explorar outras transformações disponíveis.

_Este notebook faz parte do [currículo de visualização de dados](https://github.com/uwdata/visualization-curriculum)._


In [1]:
import pandas as pd
import altair as alt

## A tabela de dados sobre filmes

Trabalharemos com uma tabela de dados (_dataset_) sobre filmes, extraída da coleção [vega-datasets](https://vega.github.io/vega-datasets/). Os dados incluem variáveis como o nome do filme, diretor, gênero, data de lançamento, classificações e receitas brutas. No entanto, _tenha cuidado ao trabalhar com esses dados_: os filmes são de anos com amostras desiguais usando dados combinados de múltiplas fontes. Se você analisar com mais detalhe, encontrará problemas como valores ausentes e até alguns erros sutis! Mesmo assim, os dados devem ser interessantes para explorar...

Vamos obter a URL do arquivo JSON de dados a partir do pacote vega_datasets e, em seguida, carregar os dados em um DataFrame do Pandas para que possamos inspecionar seu conteúdo.


In [2]:
movies_url = 'https://cdn.jsdelivr.net/npm/vega-datasets@1/data/movies.json'
movies = pd.read_json(movies_url)

Quantas linhas (registros) e colunas (campos) existem no _dataset_ de filmes?

In [75]:
movies.shape

(3201, 16)

Agora, vamos dar uma olhada nas primeiras 5 linhas da tabela para entender melhor os campos e os tipos de dados...

In [76]:
movies.head(5)

Title   US_Gross  Worldwide_Gross  US_DVD_Sales  \
0              The Land Girls   146083.0         146083.0           NaN   
1      First Love, Last Rites    10876.0          10876.0           NaN   
2  I Married a Strange Person   203134.0         203134.0           NaN   
3        Let's Talk About Sex   373615.0         373615.0           NaN   
4                        Slam  1009819.0        1087521.0           NaN   

   Production_Budget Release_Date MPAA_Rating  Running_Time_min Distributor  \
0          8000000.0  Jun 12 1998           R               NaN    Gramercy   
1           300000.0  Aug 07 1998           R               NaN      Strand   
2           250000.0  Aug 28 1998        None               NaN   Lionsgate   
3           300000.0  Sep 11 1998        None               NaN   Fine Line   
4          1000000.0  Oct 09 1998           R               NaN     Trimark   

                Source Major_Genre         Creative_Type Director  \
0                 None        None                  None     None   
1                 None       Drama                  None     None   
2                 None      Comedy                  None     None   
3                 None      Comedy                  None     None   
4  Original Screenplay       Drama  Contemporary Fiction     None   

   Rotten_Tomatoes_Rating  IMDB_Rating  IMDB_Votes  
0                     NaN          6.1      1071.0  
1                     NaN          6.9       207.0  
2                     NaN          6.8       865.0  
3                    13.0          NaN         NaN  
4                    62.0          3.4       165.0

## Histogramas

Vamos começar nosso tour pelas tranformações _dividindo_ os dados em gupos discretos e _contando_ os registros para resumir esses grupos. Os gráficos que resultam disso são conhecidos como [_histogramas_](https://pt.wikipedia.org/wiki/Histograma).

Primeiro, vamos observar os dados não agregados: um gráfico de dispersão mostrando avaliações de filmes do site Rotten Tomatoes versus as avaliações de usuários da plataforma IMDB. Vamos providenciar o dados ao Altair passando a URL dos dados do filme para o método `Chart`. (Nós também poderíamos passar o _data frame_ do Pandas diretamente para conseguirmos o mesmo resultado.) Podemos então diferenciar as avaliações do Rotten Tomatoes e IMDB utilizando os canais `x` e `y`:

In [3]:
alt.Chart(movies_url).mark_circle().encode(
    alt.X('Rotten_Tomatoes_Rating:Q'),
    alt.Y('IMDB_Rating:Q')
)

alt.Chart(...)

Para resumir esses dados, podemos separar um campo de dados para agrupar valores numéricos em grupos discretos. Aqui, nós separamos no eixo x utilizando o parâmetro `bin=True` no canal de codificação `x`. O resultado é um conjunto de dez partições com mesmo tamanho de intervalo, cada uma correspondendo a uma gama de dez pontos de avaliação diferentes.

In [4]:
alt.Chart(movies_url).mark_circle().encode(
    alt.X('Rotten_Tomatoes_Rating:Q', bin=True),
    alt.Y('IMDB_Rating:Q')
)

alt.Chart(...)

Configurar `bin=True` utiliza a configuração padrão de particionamento, porém, conseguimos ter mais controle sobre esse parâmetro se desejarmos. Vamos ajustar a contagem máxima de partições (`maxbins`) para 20, a qual tem o efeito de dobrar o número de partições. Agora cada parte corresponde a uma gama de cinco pontos de avaliação.

In [5]:
alt.Chart(movies_url).mark_circle().encode(
    alt.X('Rotten_Tomatoes_Rating:Q', bin=alt.BinParams(maxbins=20)),
    alt.Y('IMDB_Rating:Q')
)

alt.Chart(...)

Com os dados repartidos, vamos agora resumir a distribuição das avalições do Rotten Tomatoes. Vamos deixar de lado as avaliações do IMDB por enquanto, e no lugar disso, vamos usar o canal de codificação `y` para exibir uma contagem (`count`) agregada dos registros, de modo que a posição vertical de cada ponto indica o número de filmes por avaliação (considerando as partições) do Rotten Tomatoes.

Como o agregador `count` conta o número total de registros em cada repartição indepedentemente do valor do campo, não precisamos incluir um nome de campo na codificação `y`.

In [6]:
alt.Chart(movies_url).mark_circle().encode(
    alt.X('Rotten_Tomatoes_Rating:Q', bin=alt.BinParams(maxbins=20)),
    alt.Y('count()')
)

alt.Chart(...)

Para chegarmos em um histograma padrão, vamos mudar o tipo de marca de círculo (`circle`) para barra (`bar`):

In [7]:
alt.Chart(movies_url).mark_bar().encode(
    alt.X('Rotten_Tomatoes_Rating:Q', bin=alt.BinParams(maxbins=20)),
    alt.Y('count()')
)

alt.Chart(...)

_Podemos agora examinar a distribuição de avaliações mais claramente: podemos ver menos filmes na faixa negativa e um pouco mais de filmes com notas maiores, mas de maneira geral obsevamos uma distribuição uniforme. Avaliações do Rotten Tomatoes são determinadas utilizando "joinha" e "deslike" dos críticos de filme e calculando a porcentagem de reações positivas. Essa abordagem aparenta realizar um bom trabalho utilizando toda faixa dos valores das avaliações._

Similarmente, podemos criar um histograma para as avaliações do IMDB trocando apenas o campo no canal de codificação `x`: 

In [8]:
alt.Chart(movies_url).mark_bar().encode(
    alt.X('IMDB_Rating:Q', bin=alt.BinParams(maxbins=20)),
    alt.Y('count()')
)

alt.Chart(...)

_Em contraste com a distribuição uniforme que vimos antes, as classificações do IMDB exibem uma distribuição em forma de sino (embora esteja [negativamente distorcida](https://en.wikipedia.org/wiki/Skewness)). As classificações do IMDB são formadas pela média das pontuações (que variam de 1 a 10) fornecidas pelos usuários do site. Podemos ver que esta forma de medição leva a um formato diferente das classificações do Rotten Tomatoes. Podemos notar também que a moda da distribuição está entre 6.5 e 7: as pessoas geralmente gostam de ver filmes, o que explica potencialmente o viés positivo!_

Agora devemos voltar ao nosso gráfico de dispersão das classificações do Rotten Tomatoes e do IMDB. Aqui está o que acontece se descartarmos _ambos_ os eixos do nosso gráfico original.

In [9]:
alt.Chart(movies_url).mark_circle().encode(
    alt.X('Rotten_Tomatoes_Rating:Q', bin = alt.BinParams(maxbins = 20)),
    alt.Y('IMDB_Rating:Q', bin = alt.BinParams(maxbins = 20))
)

alt.Chart(...)

Os detalhes são perdidos devido ao _excesso de plotagens_, onde muitos pontos estão desenhados diretamente uns sobre os outros.

Para formar um histograma bidimensional, podemos adicionar um agregador `count` como antes. Como os canais de codificação `x` e `y` já estão em uso, devemos usar um canal de codificação diferente para transmitir as contagens. Aqui está o resultado do uso de área circular, adicionando um canal de codificação de tamanho (`size`).

In [10]:
alt.Chart(movies_url).mark_circle().encode(
    alt.X('Rotten_Tomatoes_Rating:Q', bin = alt.BinParams(maxbins = 20)),
    alt.Y('IMDB_Rating:Q', bin = alt.BinParams(maxbins = 20)),
    alt.Size('count()')
)

alt.Chart(...)

De forma alternativa, podemos codificar contagens usando o canal cor (`color`) e alterar o tipo de marca para barra (`bar`). O resultado é um histograma bidimensional na forma de um _[heatmap](https://en.wikipedia.org/wiki/Heat_map)_.

In [88]:
alt.Chart(movies_url).mark_bar().encode(
    alt.X('Rotten_Tomatoes_Rating:Q', bin = alt.BinParams(maxbins = 20)),
    alt.Y('IMDB_Rating:Q', bin = alt.BinParams(maxbins = 20)),
    alt.Color('count()')
)

alt.Chart(...)

Compare os histogramas 2D baseados em tamanho e cor acima. Qual codificação você acha que deveria ser preferida? Por que? Em qual gráfico você pode comparar com mais precisão a magnitude dos valores individuais? Em qual gráfico você consegue ver com mais precisão a densidade geral das avaliações?

## Agregação (Eliani)

As contagens são apenas um tipo de resumo. Podemos também calcular resumos usando medidas como a média (`average`), mediana (`median`), mínimo (`min`), ou máximo (`max`). A documentação do Altair inclui o [conjunto completo de funções de resumo disponíveis](https://altair-viz.github.io/user_guide/transform/aggregate.html#user-guide-aggregate-transform).

Vamos dar uma olhada em alguns exemplos!

### Médias e ordenação (Eliani)

_Diferentes gêneros de filmes recebem de forma consistente diferentes classificações dos críticos?_ Como um primeiro passo para responder a esta pergunta, podemos examinar a [média (também conhecida como *média aritmética*)](https://en.wikipedia.org/wiki/Arithmetic_mean) de classificação para cada gênero de filme.

Vamos visualizar o gênero ao longo do eixo ``y`` e traçar a classificação média do Rotten Tomatoes ao longo do eixo ``x``.


In [11]:
alt.Chart(movies_url).mark_bar().encode(
    alt.X('average(Rotten_Tomatoes_Rating):Q'),
    alt.Y('Major_Genre:N')
)

alt.Chart(...)

_Parece haver alguma variação interessante, mas olhar para os dados como uma lista alfabética não é muito útil para classificar as respostas da crítica aos gêneros._

Para uma imagem mais organizada, vamos ordenar os gêneros por ordem decrescente de classificação média. Para fazermos isso, vamos adicionar um parâmetro ordem
(`sort`) ao canal de codificação `y`, indicando que queremos ordenar pela média (`op`, a operação de agregação) da classificação do *Rotten Tomatoes* (o 
`field`) por ordem (`order`) decrescente.

In [12]:
alt.Chart(movies_url).mark_bar().encode(
    alt.X('average(Rotten_Tomatoes_Rating):Q'),
    alt.Y('Major_Genre:N', sort=alt.EncodingSortField(
        op='average', field='Rotten_Tomatoes_Rating', order='descending')
    )
)

alt.Chart(...)

_A ordenação sugere que os críticos apreciam muito os documentários, os musicais, os faroestes e os dramas, mas desprezam as comédias românticas e os filmes de terror... e quem não gosta de filmes com gênero desconhecido (`null`)?_

<!--### Medians and the Inter-Quartile Range

While averages are a common way to summarize data, they can sometimes mislead. For example, very large or very small values ([*outliers*](https://en.wikipedia.org/wiki/Outlier)) might skew the average. To be safe, we can compare the genres according to the [*median*](https://en.wikipedia.org/wiki/Median) ratings as well.

The median is a point that splits the data evenly, such that half of the values are less than the median and the other half are greater. The median is less sensitive to outliers and so is referred to as a [*robust* statistic](https://en.wikipedia.org/wiki/Robust_statistics). For example, arbitrarily increasing the largest rating value will not cause the median to change.

Let's update our plot to use a `median` aggregate and sort by those values:-->

### Medianas e intervalo interquartil (Erique)

Embora as médias sejam uma forma comum de resumir dados, às vezes podem ser enviesadas. Por exemplo, valores muito grandes ou muito pequenos ([*outliers*](https://en.wikipedia.org/wiki/Outlier)) podem distorcer a média. Por segurança, também podemos comparar os dados de acordo com a [*mediana*](https://en.wikipedia.org/wiki/Median) das classificações.

A mediana é um ponto que divide os dados uniformemente, de forma que metade dos valores seja menor que a mediana e a outra metade seja maior. A mediana é menos sensível a valores discrepantes e, portanto, é chamada de [estatística *robusta*](https://en.wikipedia.org/wiki/Robust_statistics). Por exemplo, aumentar arbitrariamente o maior valor de classificação não fará com que a mediana mude.

Vamos atualizar nosso gráfico para usar um agregador de mediana (`median`) e classificar por esses valores:

In [13]:
alt.Chart(movies_url).mark_bar().encode(
    alt.X('median(Rotten_Tomatoes_Rating):Q'),
    alt.Y('Major_Genre:N', sort=alt.EncodingSortField(
        op='median', field='Rotten_Tomatoes_Rating', order='descending')
    )
)

alt.Chart(...)

<!--_We can see that some of the genres with similar averages have swapped places (films of unknown genre, or `null`, are now rated highest!), but the overall groups have stayed stable. Horror films continue to get little love from professional film critics._

It's a good idea to stay skeptical when viewing aggregate statistics. So far we've only looked at *point estimates*. We have not examined how ratings vary within a genre.

Let's visualize the variation among the ratings to add some nuance to our rankings. Here we will encode the [*inter-quartile range* (IQR)](https://en.wikipedia.org/wiki/Interquartile_range) for each genre. The IQR is the range in which the middle half of data values reside. A [*quartile*](https://en.wikipedia.org/wiki/Quartile) contains 25% of the data values. The inter-quartile range consists of the two middle quartiles, and so contains the middle 50%. 

To visualize ranges, we can use the `x` and `x2` encoding channels to indicate the starting and ending points. We use the aggregate functions `q1` (the lower quartile boundary) and `q3` (the upper quartile boundary) to provide the inter-quartile range. (In case you are wondering, *q2* would be the median.)-->

_Podemos ver que alguns dos gêneros com médias semelhantes trocaram de lugar (filmes de gênero desconhecido, ou ‘null’, agora têm as classificações mais altas!), mas os grupos gerais permaneceram estáveis. Os filmes de terror continuam a receber pouco entusiasmo dos críticos de cinema profissionais._

É uma boa ideia permanecer cético ao visualizar estatísticas agregadas. Até agora, analisamos apenas *estimativas locais*. Não examinamos como as classificações variam dentro de um gênero.

Vamos visualizar a variação entre as classificações para adicionar algumas nuances às nossas classificações. Aqui codificaremos o [*intervalo interquartil* (IQR)](https://en.wikipedia.org/wiki/Interquartile_range) para cada gênero. O IQR é o intervalo em que reside a metade intermediária dos valores dos dados. Um [*quartil*](https://en.wikipedia.org/wiki/Quartile) contém 25% dos valores dos dados. O intervalo interquartil consiste nos dois quartis intermediários e, portanto, contém os 50% intermediários. 

Para visualizar intervalos, podemos usar os canais de codificação `x` e `x2` para indicar os pontos inicial e final. Usamos as funções agregadoras `q1` (o limite do quartil inferior) e `q3` (o limite do quartil superior) para fornecer o intervalo interquartil. (Caso você esteja se perguntando, *q2* seria a mediana.)

In [14]:
alt.Chart(movies_url).mark_bar().encode(
    alt.X('q1(Rotten_Tomatoes_Rating):Q'),
    alt.X2('q3(Rotten_Tomatoes_Rating):Q'),
    alt.Y('Major_Genre:N', sort=alt.EncodingSortField(
        op='median', field='Rotten_Tomatoes_Rating', order='descending')
    )
)

alt.Chart(...)

### Unidades de Tempo (José Vitor)

_Agora vamos fazer uma pergunta completamente diferente: as bilheterias variam de acordo com a estação do ano?_

Para conseguir a resposta inicial, vamos traçar a média bruta de lucro nos Estados Unidos por mês.

Para fazer esse gráfico, use a unidade de tempo (`timeunit`) para mapear as datas de lançamento por mês (`month`) do ano. O resultado é similar a discretização, mas usando intervalos de tempo mais significativos. Outras unidades de tempo incluem ano (`year`), trimestre (`quarter`), dia do mês (`date`), dia da semana (`day`) e horas (`hours`). Há também outras unidades, chamadas compostas, como ano-mês (`yearmonth`) ou horas-minutos (`hoursminutes`). Veja a documenteção do Altair para [lista completa de unidades de tempo](https://altair-viz.github.io/user_guide/transform/timeunit.html#user-guide-timeunit-transform).



In [15]:
alt.Chart(movies_url).mark_area().encode(
    alt.X('month(Release_Date):T'),
    alt.Y('median(US_Gross):Q')
)

alt.Chart(...)

_Observando o gráfico resultante, as vendas médias de filmes nos EUA parecem aumentar em torno da temporada de sucessos de bilheteria do verão e do período de férias de fim de ano. Claro, pessoas ao redor do mundo (não apenas os EUA) vão ao cinema. Um padrão semelhante surge para a receita bruta ao redor do mundo?_

In [16]:
alt.Chart(movies_url).mark_area().encode(
    alt.X('month(Release_Date):T'),
    alt.Y('median(Worldwide_Gross):Q')
)

alt.Chart(...)

_Sim!_

## Transformação avançada de dados (José Vitor)

Os exemplos acima usam transformações (*bin*, *timeunit*, *aggregate*, *sort*) que são definidas em relação a um canal de codificação. Porém, em algumas situações você talvez queira aplicar uma cadeia de múltiplas transformações antes da visualização, ou usar transformações que não se integram em definições de codificação. Para tais casos, Altair e Vega-Lite suportam transformações de dados definidas separadamente das codificações. Essas transformações são aplicadas nos dados *antes* de qualquer codificação ser considerada.

Nós também *poderíamos* fazer transformações usando Pandas diretamente, e então visualizar o resultado. Porém, usar as transformações embutidas permite que nossas visualizações sejam publicadas mais facilmente em outros contextos; por exemplo, exportar o Vega-Lite JSON para usar em uma interface da web independente. Vamos dar uma olhada nas transformações embutidas suportadas pelo Altair como calcular (`calculate`), filtrar (`filter`), agregar (`aggregate`), e janela (`window`).


### *Calcular (`calculate`) (Pedro Henrique Barbosa)*

_Pense novamente na comparação entre a receita nos E.U.A e a receita mundial. A receita mundial não inclui os EUA? (De fato, inclui) Como podemos ter uma melhor noção das tendências fora dos EUA?_

Com a transformação `calculate` nós podemos derivar novos campos. Aqui queremos subtrair a receita dos E.U.A (`US_Gross`) da receita mundial (`Worldwide_gross`). A transformação `calculate` pega uma *string* de expressão Vega ([*Vega expression*](https://vega.github.io/vega/docs/expressions/)) para realizar uma operação sobre um único registro. *Vega expressions* utiliza sintaxe *JavaScript*. O prefixo `datum.` acessa os valores de um campo de regisro.

In [17]:
alt.Chart(movies).mark_area().transform_calculate(
    NonUS_Gross='datum.Worldwide_Gross - datum.US_Gross'
).encode( 
    alt.X('month(Release_Date):T'),
    alt.Y('median(NonUS_Gross):Q')
)

alt.Chart(...)

_Podemos observar que as tendências sazonais se mantêm fora dos EUA, mas com um declínio significativo nos meses fora dos picos._

### Filtrar (`filter`) (Pedro Henrique Barbosa)

A transformação *filter* cria uma nova tabela com um subconjunto dos dados originais, removendo linhas que não atendem a um requisito, conhecido como predicado ([*predicate*](https://en.wikipedia.org/wiki/Predicate_%28mathematical_logic%29)). Semelhante à transformação *calculate*, os *filter predicates* são aplicados utilizando a linguagem [Vega expression](https://vega.github.io/vega/docs/expressions/).

Abaixo, adicionamos um filtro para limitar nosso gráfico de dispersão inicial de classificações do IMDB vs. Rotten Tomatoes para apenas filmes do gênero principal "Comédia Romântica" (*Romantic Comedy*).

In [18]:
alt.Chart(movies_url).mark_circle().encode(
    alt.X('Rotten_Tomatoes_Rating:Q'),
    alt.Y('IMDB_Rating:Q')
).transform_filter('datum.Major_Genre == "Romantic Comedy"')

alt.Chart(...)

_Como o gráfico muda se observarmos os outros gêneros? Edite a expressão do filtro para descobrir._

Agora, vamos filtrar para ver apenas filmes lançados antes de 1970.

In [100]:
alt.Chart(movies_url).mark_circle().encode(
    alt.X('Rotten_Tomatoes_Rating:Q'),
    alt.Y('IMDB_Rating:Q')
).transform_filter('year(datum.Release_Date) < 1970')

alt.Chart(...)

_Eles parecem ter pontuações anormalmente altas! Filmes antigos são melhores que os demais ou há um viés de seleção ([selection bias](https://en.wikipedia.org/wiki/Selection%5Fbias)) a filmes mais antigos com melhor classificação neste conjunto de dados?_

### Agregação (`aggregate`) (Tainá)

Já vimos transformações com agregação (`aggregate`), como `count` e `average`, no contexto de canais de codificação. Também podemos especificar agregações separadamente, como uma etapa de pré-processamento para outras transformações (como nos exemplos da transformação `window` abaixo). A saída de uma transformação `aggregate` é uma nova tabela de dados com registros que contêm tanto os campos de `groupby` quanto as medidas agregadas calculadas.

Vamos recriar nosso gráfico de avaliações médias por gênero, mas desta vez utilizando uma transformação `aggregate` separada. A tabela de saída da transformação `aggregate` contém 13 linhas, uma para cada gênero.

Para ordenar o eixo `y`, devemos incluir uma operação de agregação obrigatória nas instruções de ordenação. Aqui utilizamos o operador `max`, que funciona bem porque há apenas um registro de saída por gênero. Poderíamos usar o operador `min` da mesma forma e obteríamos o mesmo gráfico.

In [19]:
alt.Chart(movies_url).mark_bar().transform_aggregate(
    groupby=['Major_Genre'],
    Average_Rating='average(Rotten_Tomatoes_Rating)'
).encode(
    alt.X('Average_Rating:Q'),
    alt.Y('Major_Genre:N', sort=alt.EncodingSortField(
        op='max', field='Average_Rating', order='descending'
      )
    )
)

alt.Chart(...)

### Janela (`window`) (Vinícius Prestes)

Transformações `window` realizam cálculos sobre grupos ordenados de dados. Estas transformações são ferramentas poderosas, capazes de realizar operações como ordenação, análise de avanço/atraso dos dados, soma cumulativa, somas correntes e média. Valores calculados a partir de uma transformação `window` são salvos na tabela de dados original como um novo campo de dados. As operações *window* incluem as operações de agregação vistas anteriormente, bem como operações especializadas, como `rank`, `row_number`, `lead`, e `lag`. A documentação do Vega-Lite lista [todas as operações *window* válidas](https://vega.github.io/vega-lite/docs/window.html#ops).

Uma utilidade para uma operação `window` é calcular os k primeiros elementos de uma lista. Vamos fazer um gráfico dos 20 maiores diretores em termos de lucro ao redor do mundo.

Primeiro, utilizamos o operador `filter` para remover registros em que não sabemos o diretor. Caso contrário o diretor `null` iria dominar a lista! Em seguida, aplicamos o `aggregate` para somar o lucro de cada filme, agrupado por diretor. Neste momento, poderiamos fazer um gráfico de barras ordenado, mas acabaríamos com centenas e centenas de diretores. Como podemos limitar a visualização a apenas os 20 primeiros?

A transformação `window` nos permite determinar os primeiros diretores calculando sua ordem relativa. Dentro da nossa definição da transformação `window`, podemos ordenar por lucro e usar a operação `rank` pra calcular as posições relativas àquela ordenação. Depois, podemos adicionar uma transformação `filter` para limitar os dados apenas aos registros cuja a posição é menor ou igual a 20.

In [20]:
alt.Chart(movies_url).mark_bar().transform_filter(
    'datum.Director != null'
).transform_aggregate(
    Gross='sum(Worldwide_Gross)',
    groupby=['Director']
).transform_window(
    Rank='rank()',
    sort=[alt.SortField('Gross', order='descending')]
).transform_filter(
    'datum.Rank < 20'
).encode(
    alt.X('Gross:Q'),
    alt.Y('Director:N', sort=alt.EncodingSortField(
        op='max', field='Gross', order='descending'
    ))
)

alt.Chart(...)

_Vemos que Steven Spielberg foi muito bem sucedido em sua carreira! Entretanto, mostrar as somas pode favorecer diretores que tiveram carreiras mais longas, e portanto tiveram lucros maiores com a produção de mais filmes. O que aconteceria se nós trocassemos a operação de agregação escolhida? Quem é um diretor mais bem sucedido em termos da **media** ou **mediana** dos lucros por filme? Modifique a transformação agregada acima!_

Anteriormente neste notebook, trabalhamos com histogramas, que aproximam a [*função densidade de probabilidade*](https://en.wikipedia.org/wiki/Probability_density_function) de um conjunto de valores. Uma abordagem complementar é observar a [*distribuição cumulativa*](https://en.wikipedia.org/wiki/Cumulative_distribution_function). Por exemplo, considere um histograma no qual cada _bin_ inclui não só o seu valor mas também a soma dos valores de todos os _bins_ anteriores &mdash; o resultado é uma _soma corrente_, com o último _bin_ contando o número total de registros. Um gráfico cumulativo nos mostra diretamente, dado um valor de referência, quantos dos valores nos dados são menores ou iguais à referência.

Para um exemplo concreto, vamos observar a distribuição cumulativa de filmes por tempo de duração (em minutos). Apenas um subconjunto dos registros inclui a informação sobre o tempo de duração, portanto devemos primeiro aplicar `filter` aqueles que a possuem. Em seguida, aplicamos o `aggregate` para contar o número de filmes por duração (utilizando implicitamente _bins_ de tamanho 1 minuto). Depois, utilizamos a transformação `window` para computar a soma currente do total sobre os _bins_, em ordem crescente de tempo de duração.

In [21]:
alt.Chart(movies_url).mark_line(interpolate='step-before').transform_filter(
    'datum.Running_Time_min != null'
).transform_aggregate(
    groupby=['Running_Time_min'],
    Count='count()',
).transform_window(
    Cumulative_Sum='sum(Count)',
    sort=[alt.SortField('Running_Time_min', order='ascending')]
).encode(
    alt.X('Running_Time_min:Q', axis=alt.Axis(title='Duration (min)')),
    alt.Y('Cumulative_Sum:Q', axis=alt.Axis(title='Cumulative Count of Films'))
)

alt.Chart(...)

_Vamos análisar a distribuição cumulativa da duração dos filmes. Podemos ver que os filmes com menos de 110 minutos compõem cerca de metade dos filmes para os quais temos a informação de duração. Podemos ver um crescimento constante entre os filmes de 90 minutos até 2 horas de duração, a partir do qual a distribuição começa a estabilizar. Apesar de raros, o dataset contém diversos filmes com mais de 3 horas de duração!_



## Resumo (Armando)

 Nesta seção, apresentamos apenas uma prévia do poder da transformação de dados! Para mais detalhes, incluindo todas as transformações disponíveis e seus parâmetros, veja a [ documentação de transformação de dados do Altair](https://altair-viz.github.io/user_guide/transform/index.html).

Às vezes, você precisará executar uma transformação de dados significativa para preparar seus dados _antes mesmo_ de usar ferramentas de visualização. Para se envolver com preparação de dados ([_data wrangling_](https://en.wikipedia.org/wiki/Data_wrangling)), através do próprio Python, você pode usar a [biblioteca Pandas](https://pandas.pydata.org/).
                                                                                                                                           

Agora faremos alguns exemplos daquilo que foi aprendido hoje:

## Exemplos

In [22]:
from vega_datasets import data

### Exemplo 1:  (Armando)

In [23]:
df = data.disasters()

In [24]:
df.groupby('Entity').sum

<bound method GroupBy.sum of <pandas.core.groupby.generic.DataFrameGroupBy object at 0x0000020BFF623C80>>

Farei as duas visualizações referentes ao meu exemplo a partir do data frame `disaster`. Essa base de dados fornece o números de mortes em cada ano devido a uma causa específica. Pelo menos foi isso que percebi a principio. No desenvolvimento a seguir irei investigar isso

#### Estatísticas de resumo
Primeiramente quero saber sobre quais tipos de mortes essa base trata, a quantidade de mortos de cada categoria e a quantidade de mortes por ano, tudo em ordem decrescente de incidência. Vou usar o comundo `groupby`para resolver isso

In [25]:
df

Entity  Year   Deaths
0    All natural disasters  1900  1267360
1    All natural disasters  1901   200018
2    All natural disasters  1902    46037
3    All natural disasters  1903     6506
4    All natural disasters  1905    22758
..                     ...   ...      ...
798               Wildfire  2013       35
799               Wildfire  2014       16
800               Wildfire  2015       67
801               Wildfire  2016       39
802               Wildfire  2017       75

[803 rows x 3 columns]

In [26]:
df_grouped_sorted1 = df.groupby('Entity', as_index=False)['Deaths'].sum().sort_values(by='Deaths', ascending=False)
df_grouped_sorted1

Entity    Deaths
0   All natural disasters  32607156
1                 Drought  11731294
3                Epidemic   9596463
6                   Flood   6954992
2              Earthquake   2576801
5         Extreme weather   1396601
4     Extreme temperature    182604
9       Volcanic activity     96366
7               Landslide     63068
8     Mass movement (dry)      5030
10               Wildfire      3925

Quero obter alguma estatística desses dados, asim usarei o comando `describe`.

In [27]:
df_grouped_sorted1.describe()

Deaths
count  1.100000e+01
mean   5.928573e+06
std    9.814903e+06
min    3.925000e+03
25%    7.971700e+04
50%    1.396601e+06
75%    8.275728e+06
max    3.260716e+07

In [28]:
df_grouped_sorted2 = df.groupby('Year', as_index=False)['Deaths'].sum().sort_values(by='Deaths', ascending=False)
df_grouped_sorted2

Year   Deaths
30   1931  7412454
19   1920  6408448
27   1928  6009790
16   1917  5047014
58   1959  4026484
..    ...      ...
37   1938     4450
116  2017     4174
12   1913     1764
15   1916      600
13   1914      578

[117 rows x 2 columns]

Novamente usando o `describe`

In [29]:
df_grouped_sorted2.describe()

Year        Deaths
count   117.000000  1.170000e+02
mean   1958.965812  5.573872e+05
std      33.976902  1.339978e+06
min    1900.000000  5.780000e+02
25%    1930.000000  2.794600e+04
50%    1959.000000  5.978600e+04
75%    1988.000000  2.402620e+05
max    2017.000000  7.412454e+06

De forma menos clara que um gráfico, essas estatísticas mostram que a variação no número de mortes devido a causa da morte é maior que devido ao ano. Isso poderá ser confirmado ou contestado com as leituras dos graficos bidimensionais.

#### Análises unidimensionais e bidimensionais
Farei dois gráficos, um que relaciona morte com causa e outro que relaciona morte com ano.

In [30]:
#Gráfico morte vs causa
chart = alt.Chart(df_grouped_sorted1).mark_bar().encode(
    y=alt.Y('Deaths:Q', title='Total de Mortes'),
    x=alt.X('Entity:N', sort='-x', title='Tipo de Desastre'),
    color=alt.Color('Entity:N', legend=None)  # Remove a legenda de cores
).properties(
    width=800,
    height=500,
    title="Total de Mortes por categoria"
)

chart

alt.Chart(...)

In [31]:
# Gráfico morte vs ano
chart = alt.Chart(df_grouped_sorted2).mark_bar().encode(
    y = alt.Y('Deaths:Q', title = 'Total de mortes'),
    x = alt.X('Year:O', sort='ascending',title = 'ano'),
    color = alt.Color('Year:O', legend=None)
).properties(
    width=1200,
    height=500,
    title="Total de Mortes por ano"
)
chart

alt.Chart(...)

Para melhorar a visualização irei agrupar de 3 em 3 anos

In [32]:
df['Year_Group'] = (df['Year'] // 3) * 3  # Exemplo: 1900-1902, 1903-1905, etc.


chart = alt.Chart(df).mark_bar().encode(
    x=alt.X('Year_Group:O', title='Intervalo de 3 Anos', sort='ascending'),
    y=alt.Y('sum(Deaths):Q', title='Total de Mortes'),
    tooltip=['Year_Group', 'sum(Deaths)']
).properties(
    width=800,
    height=400,
    title="Histograma de Mortes por Intervalo de 3 Anos"
)
chart

alt.Chart(...)

#### Visualização 1
Com essas informações em mãos irei criar um gráfico que junta informação de quantidade, causa e ano das mortes:

In [33]:
df['Year_Group'] = (df['Year'] // 3) * 3  # Exemplo: 1900-1902, 1903-1905, etc.

# Criar o histograma no Altair
chart = alt.Chart(df).mark_bar().encode(
    x=alt.X('Year_Group:O', title='Intervalo de 3 Anos', sort='ascending'),
    y=alt.Y('sum(Deaths):Q', title='Total de Mortes'),
    color = alt.Color('Entity:O', scale=alt.Scale(scheme='category20b')),
    tooltip=['Year_Group', 'sum(Deaths)', 'Entity']
).properties(
    width=800,
    height=600,
    title="Histograma de Mortes por Intervalo de 3 Anos"
)
chart

alt.Chart(...)

#### Visualização 2
Para a segunda visualização foi pensado um gráfico que rastrease de forma mais contínua a incidencia de mortes. Assim podemos ver que as causas de mortes passaram a ser mais uniformes com o decorrer do tempo.

In [34]:
# Criar o heatmap
heatmap = alt.Chart(df).mark_rect().encode(
    x=alt.X('Year:O', title='Ano'),
    y=alt.Y('Entity:N', title='Tipo de Desastre'),
    color=alt.Color('Deaths:Q', title='Número de Mortes',
                    scale=alt.Scale(scheme='reds')),
    tooltip=['Entity', 'Year', 'Deaths']
).properties(
    width=900,
    height=500,
    title='Heatmap de Mortes por Desastres Naturais ao Longo dos Anos'
)

heatmap


alt.Chart(...)

### Exemplo 2: (David)

In [35]:
df = data.driving()

Para este trabalho, farei x exemplos com base no dataframe `driving`. Essa base de dados possui informações referentes ao deslocamento (não há informações sobre quem se desloca), direção (também não é explicado à que se refere essa direção) e o preço da gasolina em cada ano. A característcias que iremos observar aqui serão a relação entre a distância percorrida e o preço da gasolina, além de observar como se deu a distribuição do preço da gasolina ao longo dos anos observados.

In [36]:
df.head(10)

side  year  miles   gas
0    left  1956   3675  2.38
1   right  1957   3706  2.40
2  bottom  1958   3766  2.26
3     top  1959   3905  2.31
4   right  1960   3935  2.27
5  bottom  1961   3977  2.25
6   right  1962   4085  2.22
7  bottom  1963   4218  2.12
8  bottom  1964   4369  2.11
9  bottom  1965   4538  2.14

#### Estatísticas de resumo
Primeiro, queremos saber como são definidas as variáveis de nosso dataframe, para então realizarmos a análise das estatísticas de resumo. Em nosso dataframe, temos apenas quatro variáveis, vamos separá-las e determinar quais os tipos de cada uma:
- side: Nominal
- year: Ordinal
- miles: Quantitativa
- gas: Quantitativa

Em nosso caso, existem apenas três variáveis que faz sentido analisarmos (para o caso da variável "side", podemos anlisar a moda relacionada a ela), para fazermos isso, utilizaremo o comando `describe` para cada uma das variáveis:

In [37]:
# Aqui, fazemos a análise apenas da variável miles.
df['miles'].describe()

count       55.000000
mean      7164.909091
std       2160.081671
min       3675.000000
25%       5291.500000
50%       6943.000000
75%       9304.000000
max      10067.000000
Name: miles, dtype: float64

In [38]:
# Aqui, fazemos a análise apenas da variável gas.
df['gas'].describe()

count    55.000000
mean      2.165091
std       0.458002
min       1.390000
25%       1.775000
50%       2.140000
75%       2.370000
max       3.310000
Name: gas, dtype: float64

Agora, para analisarmos qual a moda na variável "side", podemos elaborar um gráfico para realizar a contagem de cada uma das direções.

In [39]:
# Criar um gráfico de barras para contar cada categoria de "side"
chart = alt.Chart(df).mark_bar().encode(
    x=alt.X("side:N", title="Lado da Direção"),  # 'N' significa nominal/categórico
    y=alt.Y("count():Q", title="Contagem"),  # Conta a quantidade de cada categoria
    color="side:N"
).properties(
    title="Contagem de Cada 'Side' no Dataset Driving"
)
chart

alt.Chart(...)

Vemos que a direção que mais aparece é "right", portanto, a moda da variável 'side' é 'right'.

#### Análise unidimensional e bidimensional
Para a análise unidimensional, fizemos o gráfico acima. Já para a bidimensional, vamos elaborar um gráfico que relaciona o preço da gasolina com a distância percorrida.

In [40]:
# Gráfico morte vs ano
chart = alt.Chart(df).mark_bar().encode(
    y = alt.Y('miles:Q'),
    x = alt.X('gas:Q'),
    color = alt.Color('year:N', legend=None),
    tooltip=['miles','year','gas']
).properties(
    width=500,
    height=300,
)
chart

alt.Chart(...)

Considerando as somente as cores, vemos que, quanto menor o preço da gasolina, maior é a quantidade de milhas percorridas, entretanto, vemos que, quando o preço da gasolina atingio=u seu maior valor, as milhas percorridas em tal ano foram igualmente grandes às com a gasolina com preço baixo, isso se deve ao fato de esse aumento no preço ter ocorrido em pleno século 21, onde a utilização de veículos se faz essencial, por isso, esse dado não segue o padrão observado.

#### Visualização 1
Para a visualização vamos primeiro elaborar um histograma que apresenta o preço da gasolina a cada ano, em seguida, utilizando os conhecimentos do capítulo, vamos fazer uma ordenação para entrender quais foram os anos tais que o preço da gasolina atingiu o mínimo.

In [41]:

chart = alt.Chart(df).mark_bar().encode(
    y = alt.Y('year:O'),
    x = alt.X('gas:Q'),
    tooltip=['miles','gas']
).properties(
    width=700,
    height=600,
)
chart

alt.Chart(...)

Para ordená-lo, utilizaremos o parâmetro "sort" no eixo y para ordenar com base no preço da gasolina.

In [42]:

chart = alt.Chart(df).mark_bar().encode(
    y = alt.Y('year:O',sort=alt.EncodingSortField(
        op='max', field='gas', order='descending')),
    x = alt.X('gas:Q'),
    tooltip=['miles','gas']
).properties(
    width=700,
    height=600,
)
chart

alt.Chart(...)

Observando apenas o primeiro gráfico, podemos ver como ocorre a variação do preço da gasolina de maneira clara. Em contrapartida, com o gráfico ordenado em relação ao preço do combustível, não é possível observar essa variação de forma clara, entretanto, podemos analisar os anos em que o preço da gasolina foi menos, para então analisar os fatores que contribuíram para o preço baixo, e utilizar desse conhecimento para talvez aplicá-lo nos dias de hoje.

#### Visualização 2
Para a segunda visualização, vamos elaborar um gráfico para observar o comportamento no preço da gasolina ao longo dos anos analisados. Para uma visualização um pouco mais intuitiva, vamos definir vermelho para o aumento no preço (pois é algo ruim) e verde para a queda, para colocarmos tal condição, utilizamos a função `condition`

In [124]:

chart = alt.Chart(df).transform_window(
    prev_gas="lag(gas)",
).transform_calculate(
    pct_change="(datum.gas - datum.prev_gas) / datum.prev_gas * 100"
).mark_bar().encode(
    x=alt.X("year:O"),
    y=alt.Y("pct_change:Q", title="Yearly % Change in Gas Prices"),
    color=alt.condition(
        "datum.pct_change > 0",
        alt.value("red"),
        alt.value("green")
    )
).properties(
    title="Yearly Percentage Change in Gas Prices"
)
chart

alt.Chart(...)

Além desse exemplo, para um que mais condiz com o estudado no capítulo, vamos observar a média de milhas percorridas ao longo do tempo considerando períodos de 4 anos, para vermos o crescimento da distância percorrida ao longo do tempo.

In [137]:
# Carregar o dataset
df = data.driving()

# Criar um gráfico de barras com agregação por intervalo de anos
chart = alt.Chart(df).mark_bar().encode(
    x=alt.X("year:O",bin=alt.BinParams(step=4), title="Intervalo de Anos"),  # Agrupa a cada 10 anos
    y=alt.Y("mean(miles):Q", title="Média de Milhas por Ano"),  # Média das milhas
    tooltip=["year:O", "mean(miles):Q"]  # Adiciona tooltip
).properties(
    title="Média de Milhas Percorridas por Intervalos de 10 Anos"
)

# Mostrar o gráfico
chart.show()


alt.Chart(...)

### Exemplo 3: Cevada (Eliani)

Neste exemplo utilizarei o data set `barley` para implementar o que vimos neste capítulo.

In [46]:
# Listar os datasets disponíveis inspecionando os atributos do módulo 'data'
#print(dir(vega_datasets.data))

cevada = vega_datasets.data.barley()

# Visualizando o arquivo escolhido:
df = pd.DataFrame(cevada)
print(df.head(5))

# Quantidade de linhas e colunas:
cevada.shape

      yield    variety  year             site
0  27.00000  Manchuria  1931  University Farm
1  48.86667  Manchuria  1931           Waseca
2  27.43334  Manchuria  1931           Morris
3  39.93333  Manchuria  1931        Crookston
4  32.96667  Manchuria  1931     Grand Rapids


(120, 4)

Vamos renomear as colunas para melhor entendimento:

In [47]:
# Renomear as colunas
cevada = cevada.rename(columns={
    'year': 'ano',
    'site': 'local',
    'variety': 'variedade',
    'yield': 'rendimento'
})

# Exibir as primeiras linhas para verificar
print(cevada.head())

   rendimento  variedade   ano            local
0    27.00000  Manchuria  1931  University Farm
1    48.86667  Manchuria  1931           Waseca
2    27.43334  Manchuria  1931           Morris
3    39.93333  Manchuria  1931        Crookston
4    32.96667  Manchuria  1931     Grand Rapids


Perceba que esse data frame possui 4 colunas, sendo duas variáveis categóricas (variedade e local), uma variável ordinal (ano) e uma variável quantitativa (rendimento). Para entendermos melhor o que a variável rendimento representa, na linha 0 por exemplo, temos o 27, ou seja foi observado que em cada _acre_ de terra cultivada em <span style="color:deeppink">University Farm</span> foram produzidas 27 <span style="color:deeppink">bushels</span> (uma unidade de volume usada para medir quantidades de produtos agrícolas) de cevada.

#### Resumo Estatístico:

In [48]:
alt.Chart(cevada).mark_circle().encode(
    alt.X('variedade:N'),
    alt.Y('count()', title='Contador de frequência')
)

alt.Chart(...)

Perceba que temos ao todo 10 variedades e a  mesma quantidade de dados para cada variedade. Vamos agora calcular a média do rendimento para cada variedade:

In [49]:
alt.Chart(cevada).mark_bar().encode(
    alt.X('average(rendimento):Q', title='Média do rendimento'),
    alt.Y('variedade:N')
)

alt.Chart(...)

Os valores das médias para cada variedade estão entre 30 e 40, ou seja não parecem distoar muito. Vamos ordenar em ordem decrescente e posteriormente também ordenar pela mediana:

In [50]:
alt.Chart(cevada).mark_bar().encode(
    alt.X('average(rendimento):Q',  title='Média do rendimento'),
    alt.Y('variedade:N', sort=alt.EncodingSortField(
        op='average', field='rendimento', order='descending')
    )
)

alt.Chart(...)

In [51]:
alt.Chart(cevada).mark_bar().encode(
    alt.X('median(rendimento):Q', title='Mediana do rendimento'),
    alt.Y('variedade:N', sort=alt.EncodingSortField(
        op='median', field='rendimento', order='descending')
    )
)

alt.Chart(...)

Agora temos uma informação relevante: Apesar da variedade No.462 estar em quarto lugar com relação a média de rendimento, quando olhamos para sua mediana, ela cai para a nona posição, mostrando que a mesma possui uma maior variação no rendimento. Por outro lado, as três variedades que ocupam as primeiras posições na média, também a ocupam na mediana, mostrando que o rendimento delas é mais previsível e melhor se comparado com as outras variedades.
Vamos agora analisar o intervalo entre o primeiro e terceiro quartil:

In [52]:
alt.Chart(cevada).mark_bar().encode(
    alt.X('q1(rendimento):Q', title='Q1 do rendimento'),
    alt.X2('q3(rendimento):Q', title='Q3 do rendimento'),
    alt.Y('variedade:N', sort=alt.EncodingSortField(
        op='median', field='rendimento', order='descending')
    )
)

alt.Chart(...)

Vamos agora analisar a quantidade de cada variedade em cada ano:

In [53]:
# Gráfico separando por ano
alt.Chart(cevada).mark_bar().encode(
    x='variedade:N',              # Eixo X será as variedades
    y='count():Q', # Contagem de registros para cada variedade
    color='ano:N',                 # Cor separando os anos
    column='ano:N',                # Criar uma coluna para cada ano (gráfico separado por ano)
    tooltip=['variedade:N', 'count():Q', 'ano:N']  # Exibir informações ao passar o mouse
).properties(
    title='Quantidade de Registros por Variedade de Cevada por Ano'
)

alt.Chart(...)

Perceba que temos a mesma quantidade de cada variedade por ano. Com isso podemos analisar a média ou a mediana por ano para verificar se determinada variedade rendeu mais ou menos em um determinado ano:

In [54]:
# Gráfico de mediana com ordenação
alt.Chart(cevada).mark_bar().encode(
    x=alt.X('variedade:N', sort=alt.EncodingSortField(
        op='median', field='rendimento', order='descending')),  # Ordena pela mediana
    y='median(rendimento):Q',  # Mediana do rendimento para cada variedade
    color='ano:N',             # Cor separando os anos
    column='ano:N',            # Criar uma coluna para cada ano
    tooltip=['variedade:N', 'median(rendimento):Q', 'ano:N']  # Exibir informações ao passar o mouse
).properties(
    title='Mediana do Rendimento por Variedade de Cevada por Ano'
)

# Gráfico de média com ordenação
alt.Chart(cevada).mark_bar().encode(
    x=alt.X('variedade:N', sort=alt.EncodingSortField(
        op='average', field='rendimento', order='descending')),  # Ordena pela média
    y='average(rendimento):Q',  # Média do rendimento para cada variedade
    color='ano:N',              # Cor separando os anos
    column='ano:N',             # Criar uma coluna para cada ano
    tooltip=['variedade:N', 'average(rendimento):Q', 'ano:N']  # Exibir informações ao passar o mouse
).properties(
    title='Média do Rendimento por Variedade de Cevada por Ano'
)

alt.Chart(...)

Podemos observar que com relação a média, houve uma queda no rendimento de todas as variedades do ano 1931 para 1932. Por outro lado, com relação a mediana, algumas variedades tiveram um aumento no rendimento. Mas ainda é observado que as variedades Trebi, Wisconsin No. 38 e No. 457 permanecem com os maiores rendimentos nos dois anos. Vamos agora fazer um gráfico bidimensional que relaciona a variedade com o local de produção:

In [55]:
# Gráfico separando por local de produção
alt.Chart(cevada).mark_point().encode(
    x='variedade:N',              # Eixo X será as variedades
    y='local:N', # Contagem de registros para cada variedade
    color='ano:N',                 # Cor separando os anos
    column='ano:N',                # Criar uma coluna para cada ano (gráfico separado por ano)
    tooltip=['variedade:N', 'local:N', 'ano:N']  # Exibir informações ao passar o mouse
).properties(
    title='Local de produção por Variedade de Cevada por Ano'
)

alt.Chart(...)

Perceba que cada local produziu todas as variedades em cada ano e como vimos que cada variedade foi produzida em 12 locais e temos exatamente os mesmos 6 locais por ano, podemos deduzir que cada local tem o registro de apenas uma de cada variedade por ano. O gráfico abaixo deixa claro essa informação:

In [56]:
# Gráfico separando por local de produção com tamanho de ponto variável
alt.Chart(cevada).mark_point().encode(
    x='variedade:N',               # Eixo X será as variedades
    y='local:N',                   # Local de produção no eixo Y
    color='ano:N',                 # Cor separando os anos
    size='count():Q',              # Tamanho dos pontos proporcional à contagem de registros
    column='ano:N',                # Criar uma coluna para cada ano (gráfico separado por ano)
    tooltip=['variedade:N', 'local:N', 'count():Q', 'ano:N']  # Exibir informações ao passar o mouse
).properties(
    title='Local de Produção por Variedade de Cevada por Ano'
)

alt.Chart(...)

Uma pergunta que surge é se algum dos locais se destaca na produção de cevada, vamos verificar isso plotando o gráfico com o rendimento total por local:

In [57]:
# Agrupar os dados por 'local' e somar o 'rendimento'
cevada_rendimento_total = cevada.groupby('local')['rendimento'].sum().reset_index()

# Criar o gráfico de barras com o rendimento total por local e ordenado:
alt.Chart(cevada_rendimento_total).mark_bar().encode(
    x=alt.X('local:N', sort=alt.EncodingSortField(  # Eixo X será os locais de produção
        field='rendimento', order='descending')),   # Ordena as barras de acordo com o rendimento
    y='rendimento:Q',                               # Rendimento total por local
    color='local:N',                                # Cor separando os locais
    tooltip=['local:N', 'rendimento:Q']             # Exibir informações ao passar o mouse
).properties(
    title='Rendimento Total por Local de Produção de Cevada'
)

alt.Chart(...)

Perceba que Waseca apresenta o maior rendimento na produção de cevada. Quase o dobro da produção em Grand Rapids.

#### Conclusão:

Se queremos maximizar a produção, deve-se dar prioridade pelas variedades Trebi, Wisconsin No. 38 e No. 457 e as mesmas parecem ter uma melhor adaptação ao solo de Waseca ou ao método de cultivo e cuidado nessa região.
Podemos estudar as técnicas utilizadas na produção de cevada nessa região e tentar replicar nas outras regiões, e posteriormente verificar se há um aumento no rendimento de cevada nessas regiões.

### Exemplo 4: (Erique)

Utilizei a base de dados `us_employment` do conjunto de dados do _vega_datasets_. Para a estatística de resumo da base de dados utilizei a função `describe()`, que retorna medidas estatísticas importantes como méida, valor mínimo, valor máximo, frequências e desvio padrão.  

In [61]:
# Carregar o dataset
us_employment = data.us_employment()

# Converter a coluna 'month' para formato de data
us_employment['month'] = pd.to_datetime(us_employment['month'])

# Estatísticas de resumo
description = us_employment.describe()
print("Estatísticas de Resumo:\n", description)

Estatísticas de Resumo:
                      month        nonfarm        private  goods_producing  \
count                  120     120.000000     120.000000       120.000000   
mean   2010-12-16 04:00:00  135658.566667  113508.441667     19643.558333   
min    2006-01-01 00:00:00  129726.000000  107250.000000     17627.000000   
25%    2008-06-23 12:00:00  132504.000000  110319.250000     18297.500000   
50%    2010-12-16 12:00:00  136269.000000  114283.000000     19071.500000   
75%    2013-06-08 12:00:00  138054.250000  115852.500000     21390.750000   
max    2015-12-01 00:00:00  143093.000000  120993.000000     22631.000000   
std                    NaN    3577.782600    3706.298912      1694.206152   

       service_providing  private_service_providing  mining_and_logging  \
count         120.000000                 120.000000          120.000000   
mean       116015.008333               93864.883333          777.400000   
min        111989.000000               89507.000000     

Como há vários setores de produção a serem considerados por ano, decidi analisar os dados referentes ao primeiro mês de coleta. Isso poderia ser ajustado usando a função `interative()` juntamente com a inserção de um controle deslizante variando o data de coleta de cada dado, que representa as linhas do dataframe. Tive problemas com a função `selection_single()` e `add_selection()`do altair, as funções funcionam normalmente no google gollab, porém se tornam instáveis em ambientes como o VsCode.

Segue abaixo o script em python que gera um histograma que relaciona os setores do dataframe com sua quantidade de trabalhadores no primeiro mês de coleta:

In [62]:
# Converter a coluna 'month' para formato temporal
us_employment['month'] = pd.to_datetime(us_employment['month'])

# Analisar apenas o primeiro mês do conjunto de dados
first_month = us_employment['month'].min()
us_employment_first_month = us_employment[us_employment['month'] == first_month]

# Exibição de todos os setores
us_employment_first_month_melted = us_employment_first_month.melt(
  id_vars=['month'], var_name='sector', value_name='employment'
)

# Criação do histograma
histogram_chart = alt.Chart(us_employment_first_month_melted).mark_bar().encode(
  x=alt.X("employment:Q", bin=alt.Bin(maxbins=20), title="Número de Empregos (milhares)"),
  y=alt.Y("count()", title="Frequência"),
  color=alt.Color("sector:N", legend=alt.Legend(title="Setor")),
  tooltip=["sector:N", "employment:Q", "count()"]
).properties(title="Histograma da Distribuição de Empregos - Primeiro Mês")

# Plotagem
histogram_chart.show()

alt.Chart(...)

Essa visualização nos permite observar que os setores com menos de quarenta mil trabalhadores são mais densos no nosso conjunto de dados, ao passo que apenas alguns setores superam a marca de oitenta mil trabalhadores. Em conjuntos de dados mais distribuídos essa visualização poderá ser ainda mais útil para essa tarefa.

Segue agora uma visualização inspirada nos exemplos do tópico `3.3.1. Averages and Sorting` do livro base. Essa vizualização é particularmente útil para avaliarmos rapidamente a comparação entre setores, o critério de ordenação pela quantidade de trabalhadores deixa essa tarefa mais simples além de tornar o histograma mais organizado, segue o gráfico abaixo:

In [63]:
# Criação do histograma ordenado
ranking_chart_first_month = alt.Chart(us_employment_first_month_melted).mark_bar().transform_window(
    rank='rank(employment)',
    sort=[alt.SortField('employment', order='descending')]
).encode(
    x=alt.X("rank:O", title="Ranking"),
    y=alt.Y("employment:Q", title="Empregos (milhares)"),
    color=alt.Color("sector:N", legend=alt.Legend(title="Setor")),
    tooltip=["sector:N", "employment:Q", "rank:O"]
).properties(title="Ranking do Emprego por Setor - Primeiro Mês")

# Plotagem
ranking_chart_first_month.show()

alt.Chart(...)

### Exemplo 5: Análise de Expectativa de Vida e da População Mundial (Joênio)

Este exemplo é uma análise da expectativa de vida e da população do mundo ao longo dos anos. Neste caso, estaremos empregando a biblioteca Altair e o dados de Gapminder para gerar análises estatísticas e visualizações informativas, como gráficos de linha e mapas que representem variações geográficas de vida e população.

#### 1.Preparando o Ambiente

Primeiramente, devemos carregar os pacotes e os dados a serem trabalhados. Neste caso, o conjunto de dados utilizados foi o Gapminder, pois contém informações a respeito do desenvolvimento social de vários países:

In [64]:
dados = data.gapminder()
dados.head()

year      country  cluster       pop  life_expect  fertility
0  1955  Afghanistan        0   8891209       30.332        7.7
1  1960  Afghanistan        0   9829450       31.997        7.7
2  1965  Afghanistan        0  10997885       34.020        7.7
3  1970  Afghanistan        0  12430623       36.088        7.7
4  1975  Afghanistan        0  14132019       38.438        7.7

Além disso, precisarei de uma biblioteca extra, que irá coletar algumas informações de ID para gerar algumas análises. Assim:

In [ ]:
# ! pip install pycountry

import pycountry

#### 2. Estatísticas de Resumo

No nosso caso, o objetivo é analisar a população e a expectativa de vida dos países. Assim, escolhi as colunas de dados *year*, *country*, *pop* e *life_expect*.

A priori, podemos fazer uma análise das principais estatísticas dos dados:

##### 2.1. Análise da variável *pop*:

In [67]:
media_pop = dados['pop'].mean()
mediana_pop = dados['pop'].median()
desvio_pop = dados['pop'].std()
min_pop = dados['pop'].min()
max_pop = dados['pop'].max()
quartil_1_pop = dados['pop'].quantile(0.25)
quartil_3_pop = dados['pop'].quantile(0.75)

In [68]:
print(f'''Estatísticas de resumo para "pop":

Média: {media_pop:.2f}
Desvio Padrão: {desvio_pop:.2f}
Mínimo: {min_pop}
1° Quartil: {quartil_1_pop}
Mediana: {mediana_pop}
3° Quartil: {quartil_3_pop}
Máximo: {max_pop}
''')

Estatísticas de resumo para "pop":

Média: 56234309.02
Desvio Padrão: 155301423.22
Mínimo: 53865
1° Quartil: 4563732.0
Mediana: 12292000.0
3° Quartil: 44434445.0
Máximo: 1303182268



##### 2.2. Análise da variável *life_expect*:

In [69]:
media_life = dados['life_expect'].mean()
mediana_life = dados['life_expect'].median()
desvio_life = dados['life_expect'].std()
min_life = dados['life_expect'].min()
max_life = dados['life_expect'].max()
quartil_1_life = dados['life_expect'].quantile(0.25)
quartil_3_life = dados['life_expect'].quantile(0.75)

In [70]:
print(f'''Estatísticas para "life_expect":

Média: {media_life:.2f}
Desvio Padrão: {desvio_life:.2f}
Mínimo: {min_life:.2f}
1° Quartil: {quartil_1_life:.2f}
Mediana: {mediana_life:.2f}
3° Quartil: {quartil_3_life}
Máximo: {max_life:.2f}
''')

Estatísticas para "life_expect":

Média: 66.15
Desvio Padrão: 10.71
Mínimo: 23.60
1° Quartil: 59.96
Mediana: 69.50
3° Quartil: 73.84
Máximo: 82.60



*Observação*: Neste caso, não faz muito sentido analisar as estatísticas de colunas como 'year' ou 'country', pois estas variáveis funcionam como variáveis temporais, que estão representando o ano e o país que foram coletados os dados de *pop* e *life_expect*. Ou seja, cada ano e cada país aparece de forma periódica, o que induz estatísticas de resumo que não demonstram muitas informações.

#### 3. Análise Unidimensional e Bidimensional

Feito isso, podemos fazer a análise bidimensional dos dados.

Para começar, podemos analisar a evolução da população global ao longo de 50 anos (1955-2005). Como eu preciso de dados globais, estarei realizando a soma das respectivas populações dos países, tendo como limitação o ano da informação. Deste modo:

In [71]:
populacao_mundo = dados.groupby('year')['pop'].sum().reset_index(name = 'pop_global')
populacao_mundo

year  pop_global
0   1955  2182678196
1   1960  2394564086
2   1965  2618176519
3   1970  2906025531
4   1975  3211425244
5   1980  3500588903
6   1985  3804113397
7   1990  4133335721
8   1995  4455059580
9   2000  4749735887
10  2005  5014673090

Com isso, podemos gerar um gráfico de linhas, pois é um gráfico que facilita a visualização de tendências de crescimento, ou afins.

In [72]:
populacao_mundo_anos = alt.Chart(populacao_mundo).mark_line(
    color = 'darkred'
).encode(
    x = alt.X('year:O', title = 'Anos'),
    y = alt.Y('pop_global:Q',
              title = 'População do Mundo',
              scale = alt.Scale(type = 'linear',
                                domain = [populacao_mundo['pop_global'].min() / 1e9,
                                          populacao_mundo['pop_global'].max() / 1e9]),
        axis = alt.Axis(format = '.1f')
    ),
).transform_calculate(
    pop_em_bilhao = 'datum.pop_global / 1e9'
).encode(
    y = alt.Y('pop_em_bilhao:Q', title = 'População do Mundo (em bilhões)')
).properties(
    title = 'População Mundial ao Longo dos Anos',
    width = 800,
    height = 400
)

populacao_mundo_anos

alt.Chart(...)

Perceba que a população mundial mais que duplicou em um intervalo de 50 anos (mesmo que a nossa análise esteja restrita aos países presentes nos dados).

Além disso, é interessante notar que há uma tendência linear (a principio), o que implica que este crescimento populacional estaria (visualmente falando) se mantendo, caso pudéssemos aumentar a amostra de anos analisados.

De forma análoga, estaremos analisando a expectativa de vida ao longo do mesmo período. Para encontrarmos a expectativa de vida do mundo ao longo de um ano, devemos ponderar a expectativa de vida de um país pela sua população. Assim:

In [73]:
dados['peso'] = dados['pop']
vida_media_global = dados.groupby('year').apply(
    lambda x: (x['life_expect'] * x['peso']).sum() / x['peso'].sum()
).reset_index(name = 'expectativa_de_vida_media')

vida_media_global

C:\Users\taina\AppData\Local\Temp\ipykernel_31580\377007383.py:2: DeprecationWarning: DataFrameGroupBy.apply operated on the grouping columns. This behavior is deprecated, and in a future version of pandas the grouping columns will be excluded from the operation. Either pass `include_groups=False` to exclude the groupings or explicitly select the grouping columns after groupby to silence this warning.
  vida_media_global = dados.groupby('year').apply(


year  expectativa_de_vida_media
0   1955                  52.905719
1   1960                  52.701515
2   1965                  57.961819
3   1970                  60.617444
4   1975                  62.351616
5   1980                  63.986544
6   1985                  65.568982
7   1990                  66.898222
8   1995                  68.337490
9   2000                  69.434681
10  2005                  70.509740

Do mesmo jeito, um gráfico de linhas será gerado para visualizarmos a tendência do crescimento da expectativa de vida:

In [74]:
expectativa_vida_global = alt.Chart(vida_media_global).mark_line(
    color = 'darkblue'
).encode(
    x = alt.X('year:O', title = 'Anos'),
    y = alt.Y('expectativa_de_vida_media:Q',
              title = 'Expectativa de Vida (em anos)',
              scale = alt.Scale(type = 'linear')),
).properties(
    title = 'Expectativa de Vida Média Global ao Longo dos Anos',
    width = 800,
    height = 400
)

expectativa_vida_global

alt.Chart(...)

Primeiramente, é interessante notar como a expectativa de vida global se manteve estagnada entre anos de 1955-1960. Muito provavelmente se manteve assim por conta dos conflitos bélicos que ocorreram naquela década (como a Guerra do Vietnã ou a Guerra da Coréia).

Contudo, ao analisarmos o período sob uma perspectiva geral, percebemos o crescimento da expectativa de vida ao longo do período, com um crescimento forte no inicio dos anos 1960, e um crescimento suave ao longo dos últimos 40 anos.

Além disso, é interessante analisar estes crescimentos sob a perspectiva do globo.

O objetivo é representar estes parâmetros diretamente no mapa-mundi, o que proporcionará uma análise visual bastante intuitiva. Além disso, permitirá uma comparação clara entre os países, e possibilita possíveis padrões regionais.

Deste modo, estarei trabalhando alguns códigos que façam leitura correta de códigos:

In [75]:
mapa_mundi = alt.topo_feature(data.world_110m.url, 'countries')

def codigos(pais):
    try:
        y = int(pycountry.countries.lookup(pais).numeric)
        return y
    except:
        return None  # Infelizmente é o jeito que tratarei os países que não encontrar

Com isso, estarei filtrando os dados de ano mais antigo (1955) e mais recente (2005):

In [76]:
dados_1955 = dados[dados['year'] == 1955].copy()
dados_1955['id'] = dados_1955['country'].apply(codigos)
dados_1955 = dados_1955.dropna(subset = ['id'])
dados_1955['id'] = dados_1955['id'].astype(int)

dados_2005 = dados[dados['year'] == 2005].copy()
dados_2005['id'] = dados_2005['country'].apply(codigos)
dados_2005 = dados_2005.dropna(subset = ['id'])
dados_2005['id'] = dados_2005['id'].astype(int)

Agora, podemos visualizar a distribuição da população mundial por país em 1955 e 2005:


In [77]:
paises_pop_1955 = alt.Chart(mapa_mundi).mark_geoshape().encode(
    color = alt.Color(
        'pop:Q',
        scale = alt.Scale(scheme = 'redblue', reverse = True, type = 'log'),
        legend = alt.Legend(title = 'População Total')
    ),
    tooltip = ['country:N', 'pop:Q']
).transform_lookup(
    lookup = 'id',
    from_ = alt.LookupData(dados_1955, 'id', ['pop', 'country'])
).project(
    type = 'naturalEarth1'
).properties(
    width = 400,
    height = 400,
    title = 'Mapa da População Global em 1955'
)

paises_pop_2005 = alt.Chart(mapa_mundi).mark_geoshape().encode(
    color = alt.Color(
        'pop:Q',
        scale = alt.Scale(scheme = 'redblue', reverse = True, type = 'log'),
        legend = alt.Legend(title = 'População Total')
    ),
    tooltip = ['country:N', 'pop:Q']
).transform_lookup(
    lookup = 'id',
    from_ = alt.LookupData(dados_2005, 'id', ['pop', 'country'])
).project(
    type = 'naturalEarth1'
).properties(
    width = 400,
    height = 400,
    title = 'Mapa da População Global em 2005'
)

paises_pop_1955 | paises_pop_2005

alt.HConcatChart(...)

Neste caso, os países mais populosos são aqueles que possuem a cor vermelho-escuro mais aparente. Ou seja, podemos perceber que grande parte da população global pertencem a países do leste asiático, com a China e a Índia, mesmo analisando os diferentes períodos.

Além disso, note que estes mesmos países demonstraram um grande aumento populacional entre os anos, duplicando ou triplicando suas populações no período de 50 anos.

Agora criaremos o mapa com a expectativa de vida dos países no ano de 1955 e no ano de 2005:

In [78]:
paises_vida_1955 = alt.Chart(mapa_mundi).mark_geoshape().encode(
    color = alt.Color(
        'life_expect:Q',
        scale = alt.Scale(scheme = 'redblue', reverse = False),
        legend = alt.Legend(title = 'Vida (em anos)')
    ),
    tooltip = ['country:N', 'life_expect:Q']
).transform_lookup(
    lookup = 'id',
    from_ = alt.LookupData(dados_1955, 'id', ['life_expect', 'country'])
).project(
    type = 'naturalEarth1'
).properties(
    width = 400,
    height = 400,
    title = 'Mapa da Expectativa de Vida Global em 1955'
)

paises_vida_2005 = alt.Chart(mapa_mundi).mark_geoshape().encode(
    color = alt.Color(
        'life_expect:Q',
        scale = alt.Scale(scheme = 'redblue', reverse = False),
        legend = alt.Legend(title = 'Vida (em anos)')
    ),
    tooltip = ['country:N', 'life_expect:Q']
).transform_lookup(
    lookup = 'id',
    from_ = alt.LookupData(dados_2005, 'id', ['life_expect', 'country'])
).project(
    type = 'naturalEarth1'
).properties(
    width = 400,
    height = 400,
    title = 'Mapa da Expectativa de Vida Global em 2005'
)

paises_vida_1955 | paises_vida_2005

alt.HConcatChart(...)

Com relação a expectativa de vida, podemos notar que o crescimento se solidificou em países do norte da América ou na Europa em geral.

Na verdade, com exceção da África, os países tiveram um bom crescimento na expectativa de vida ao longo dos 50 anos.

Além disso, ao compararmos com os países com grande acréscimo populacional, podemos notar um crescimento bem robusto das suas expectativas de vidas. Ou seja, sob uma perspectiva geral, as populações dos países cresceram de forma vertiginosa, e em conjunto a isso, tivemos uma melhoria geral da qualidade de vida das populações (em geral).

### Exemplo 6: (josé)


Eu escolhi a agricultura de cevada(Barley) presente no vega dataset

#### Visualização 1:

Nessa Visualisação usei da localidade e variedade para poder indicar a performance de cada variedade em relação da região.

In [79]:
df = data.barley()

chart = alt.Chart(df).transform_aggregate(
    mean_yield="mean(yield)",
    groupby=["site", "variety"]
).mark_bar().encode(
    x=alt.X("mean_yield:Q", title="Rendimento Médio (bushels/acre)"),
    y=alt.Y("variety:N", title="Variedade", sort="-x"),
    color="variety:N",
    column=alt.Column("site:N", title="Localidade"),
    tooltip=[alt.Tooltip("variety:N"), alt.Tooltip("site:N"), alt.Tooltip("mean_yield:Q")]
).properties(
    title="Comparação do Rendimento das Variedades de Cevada por Localidade",
    width=120
)

chart.show()


alt.Chart(...)

#### Visualização 2:

Esse é feito para ver a variação entre os anos que foram medidos e como as variedades de planta se mantiam apos um ano em cada região

In [157]:

scatter_chart = alt.Chart(df).mark_point(filled=True, size=60).encode(
    x=alt.X("year:O", title="Ano"),
    y=alt.Y("yield:Q", title="Rendimento (bushels/acre)"),
    color="variety:N",
    column=alt.Column("site:N", title="Localidade"),
    tooltip=["variety", "site", "year", "yield"]
).properties(
    title="Distribuição do Rendimento das Variedades de Cevada ao Longo dos Anos",
    width=120
)

scatter_chart.show()

alt.Chart(...)

#### Conclusão

Podemos analisar como as diferentes variedades porfomaram durante os dois anos e como elas se comparam uma a outra em cada uma das regiões medidas

### Exemplo: Seattle weather (Pedro Henrique Barbosa)

Resolvi analisar os dados de Seattle. Esse *dataframe* conta com 6 atributos, dos quais um é analisado como categórico ordinal ( a data **date** ), um é categórico nominal ( o tempo/clima **weather** ) e 4 são quantitativos ( a precipitação **precipitation**, a temperatura máxima **temp_max**, a temperatura mínima **temp_min** e o vento **wind** ).


In [80]:
df = data.seattle_weather()

In [81]:
df.head(5)

date  precipitation  temp_max  temp_min  wind  weather
0 2012-01-01            0.0      12.8       5.0   4.7  drizzle
1 2012-01-02           10.9      10.6       2.8   4.5     rain
2 2012-01-03            0.8      11.7       7.2   2.3     rain
3 2012-01-04           20.3      12.2       5.6   4.7     rain
4 2012-01-05            1.3       8.9       2.8   6.1     rain

In [82]:
df.shape

(1461, 6)

Contamos com 1461 dias registrados. Podemos extrair algumas medidas de resumo desses dados. Para isso, utilizei o `average` para conhecer a média em cada ano. Aqui estão as médias com os dados precipitação (em mm para cada dia), temperatura máxima (em °C), temperatura mínima (em °C) e vento (em mph), respectiamente. As unidades usadas foram pesquisadas por fora do csv. Valores arredondados para duas casas decimais.

Médias de 2012: 3.35, 15.28, 7.30, 3.40.

Médias de 2013: 2.27, 16.06, 8.15, 3.02.

Médias de 2014: 3.38, 17.00, 8.66, 3.39.

Médias de 2015: 3.12, 17.43, 8.84, 3.16.

Médias gerais : 3.03, 16.44, 8.24, 3.24.  

In [83]:
# Precipitação

alt.Chart(df).mark_bar().encode(
    alt.X('date:T',timeUnit='year'),
    alt.Y('average(precipitation):Q'),
    alt.Tooltip('average(precipitation):Q', )
)

alt.Chart(...)

In [84]:
# Temperatura máxima

alt.Chart(df).mark_bar().encode(
    alt.X('date:T',timeUnit='year'),
    alt.Y('average(temp_max):Q'),
    alt.Tooltip('average(temp_max):Q', )
)

alt.Chart(...)

In [85]:
# Temperatura mínima

alt.Chart(df).mark_bar().encode(
    alt.X('date:T',timeUnit='year'),
    alt.Y('average(temp_min):Q'),
    alt.Tooltip('average(temp_min):Q', )
)

alt.Chart(...)

In [86]:
# Ventos

alt.Chart(df).mark_bar().encode(
    alt.X('date:T',timeUnit='year'),
    alt.Y('average(wind):Q'),
    alt.Tooltip('average(wind):Q', )
)

alt.Chart(...)

Já vimos as médias, agora vamos observar as medianas utilizando o `median`. É possível obserar uma leve diferença, por exemplo, a média das temperaturas máximas aumenta a cada ano, porém a mediana estabeleceu-se a mesma 2014 e 2015, indicando que houveram temperaturas máximas grandes em 2015 que se distanciaram um pouco mais da média, como se pode observar no primeiro gráfico de exemplo que não é está apresentando medidas de resumo. Não obtive sucesso em apresentar o gráfico com as medianas da precipitação, por isso este está faltando.

In [87]:
# Temperatura máxima

alt.Chart(df).mark_bar().encode(
    alt.X('date:T',timeUnit='year'),
    alt.Y('median(temp_max):Q'),
    alt.Tooltip('median(temp_max):Q', )
)

alt.Chart(...)

In [88]:
# Temperatura mínima

alt.Chart(df).mark_bar().encode(
    alt.X('date:T',timeUnit='year'),
    alt.Y('median(temp_min):Q'),
    alt.Tooltip('median(temp_min):Q', )
)

alt.Chart(...)

In [89]:
# Ventos

alt.Chart(df).mark_bar().encode(
    alt.X('date:T',timeUnit='year'),
    alt.Y('median(wind):Q'),
    alt.Tooltip('median(wind):Q', )
)

alt.Chart(...)

Aqui apresento meus gráficos exemplos feitos com base nas medidas de resumo. 

O primeiro mostra a faixa de variação da temperatura com o passar do tempo, nas médias podemos observar que as temperaturas estão aumentando em Seattle, com o gráfico percebemos uma leve subida na variação de temperatura. Primeiramente, pensei em executar um gráfico com `mark_line` para mostrar as linhas que representam as temperaturas mínimas e as temperaturas máximas, mas não obtive sucesso. Na segunda parte do primeiro gráfico podemos observar melhor o ano de 2012, pois adicionei o `filter`, ele filtrou para antes de 2013 (tive problema para usar o `datum`, ele não estava lendo corretamente o tempo, aprendi que devemos adicionar o `year`).

In [90]:
alt.Chart(df).mark_area().encode(
    alt.X('date:T'),
    alt.Y('min(temp_min):Q'),
    alt.Y2('max(temp_max):Q')
)

alt.Chart(...)

In [91]:
alt.Chart(df).mark_area().encode(
    alt.X('date:T'),
    alt.Y('min(temp_min):Q'),
    alt.Y2('max(temp_max):Q')
).transform_filter('year(datum.date) < 2013')

alt.Chart(...)

Para o segundo gráfico, observei as categorias do clima. A moda foi *sun* (ensolarado). As frequêncis estão no gráfico e a análise é unidimensional, pois estamos lidando com somente uma variável, o clima. 


In [92]:
alt.Chart(df).mark_bar().encode(
    alt.X('weather:N'),
    alt.Y('count():Q'),
    alt.Tooltip('count():Q'),
    alt.Color('weather:N')
)

alt.Chart(...)

Para uma análise bidimensional, resolvi trabalhar temperatura máxima vs. vento. Não percebi uma correlação significativa.

In [93]:
df['temp_max'].corr(df["wind"])

np.float64(-0.16485663487495464)

In [94]:
alt.Chart(df).mark_point(filled= True).encode(
    alt.X('temp_max:Q'),
    alt.Y('wind:Q')
)

alt.Chart(...)

### Exemplo 8: Íris (Tainá)

Vamos construir uma análise sobre a base de dados Íris, que lista informações sobre a estrutura de algumas espécies de flores.

In [95]:
iris = data.iris()

Inicialmente, vamos observar a estrutura da base de dados para entender o conteúdo de cada observação.

In [96]:
iris = data.iris()
iris.head()

sepalLength  sepalWidth  petalLength  petalWidth species
0          5.1         3.5          1.4         0.2  setosa
1          4.9         3.0          1.4         0.2  setosa
2          4.7         3.2          1.3         0.2  setosa
3          4.6         3.1          1.5         0.2  setosa
4          5.0         3.6          1.4         0.2  setosa

Temos 5 informações para cada observação:
* `sepalLength`: comprimento da sépala
* `sepalWidth`: largura da sépala
* `petalLength`: comprimento da pétala
* `petalWidth`: largura da pétala
* `species`: espécie

Vamos renomear as colunas para melhor visualização do _data frame_:

In [97]:
iris.columns = ['comprimento_sepala', 'largura_sepala', 'comprimento_petala', 'largura_petala', 'especie']
iris.head()

comprimento_sepala  largura_sepala  comprimento_petala  largura_petala  \
0                 5.1             3.5                 1.4             0.2   
1                 4.9             3.0                 1.4             0.2   
2                 4.7             3.2                 1.3             0.2   
3                 4.6             3.1                 1.5             0.2   
4                 5.0             3.6                 1.4             0.2   

  especie  
0  setosa  
1  setosa  
2  setosa  
3  setosa  
4  setosa

#### Estatísticas de resumo

Podemos analisar as características da sépala e pétala para cada uma das espécies listadas. Para isso, inicialmente, veremos quantas/quais são as espécies presentes no _data frame_.

In [98]:
iris['especie'].unique()

array(['setosa', 'versicolor', 'virginica'], dtype=object)

Temos 3 espécies listadas. Geraremos medidas de estatística descritiva para as características de cada uma delas.

In [99]:
iris[iris['especie'] == 'setosa'].describe()

comprimento_sepala  largura_sepala  comprimento_petala  largura_petala
count            50.00000       50.000000           50.000000       50.000000
mean              5.00600        3.428000            1.462000        0.246000
std               0.35249        0.379064            0.173664        0.105386
min               4.30000        2.300000            1.000000        0.100000
25%               4.80000        3.200000            1.400000        0.200000
50%               5.00000        3.400000            1.500000        0.200000
75%               5.20000        3.675000            1.575000        0.300000
max               5.80000        4.400000            1.900000        0.600000

Por meio da descrição acima é possível observar algumas características gerais das setosas. Por exemplo, o comprimento médio da sépala é de aproximadamente 5 cm, enquanto o da pétala é por volta de 1.46 cm.

Também listaremos essas descrições para a versicolor e a viginica:



In [100]:
iris[iris['especie'] == 'versicolor'].describe()

comprimento_sepala  largura_sepala  comprimento_petala  largura_petala
count           50.000000       50.000000           50.000000       50.000000
mean             5.936000        2.770000            4.260000        1.326000
std              0.516171        0.313798            0.469911        0.197753
min              4.900000        2.000000            3.000000        1.000000
25%              5.600000        2.525000            4.000000        1.200000
50%              5.900000        2.800000            4.350000        1.300000
75%              6.300000        3.000000            4.600000        1.500000
max              7.000000        3.400000            5.100000        1.800000

In [102]:
iris[iris['especie'] == 'virginica'].describe()

comprimento_sepala  largura_sepala  comprimento_petala  largura_petala
count            50.00000       50.000000           50.000000        50.00000
mean              6.58800        2.974000            5.552000         2.02600
std               0.63588        0.322497            0.551895         0.27465
min               4.90000        2.200000            4.500000         1.40000
25%               6.22500        2.800000            5.100000         1.80000
50%               6.50000        3.000000            5.550000         2.00000
75%               6.90000        3.175000            5.875000         2.30000
max               7.90000        3.800000            6.900000         2.50000

Existem variações claras entre as espécies. O comprimento da pétala, por exemplo, é, em média, maior na versicolor e na virginica do que na seposa. O mesmo ocorre com a largura da pétala, o que nos leva à conclusão de que as pétalas das seposas são pequenas quando comparadas com as outras íris.

Para visualizar melhor essas informações, vamos exibí-las por meio de _boxplots_:

In [103]:
comprimento_sepala_chart = alt.Chart(iris).mark_boxplot().encode(
    alt.Y('comprimento_sepala:Q', title="Comprimento da sépala"),
    alt.Column('especie:N', title='Espécie'),
    alt.Color('especie:N', legend=alt.Legend(title="Espécie"))
).properties(
  width=50,
  height=300
)

largura_sepala_chart = alt.Chart(iris).mark_boxplot().encode(
    alt.Y('largura_sepala:Q', title="Largura da sépala"),
    alt.Column('especie:N', title='Espécie'),
    alt.Color('especie:N', legend=alt.Legend(title="Espécie"))
).properties(
  width=50,
  height=300
)

comprimento_petala_chart = alt.Chart(iris).mark_boxplot().encode(
    alt.Y('comprimento_petala:Q', title="Comprimento da pétala"),
    alt.Column('especie:N', title='Espécie'),
    alt.Color('especie:N', legend=alt.Legend(title="Espécie"))
).properties(
  width=50,
  height=300
)

largura_pétala_chart = alt.Chart(iris).mark_boxplot().encode(
    alt.Y('largura_petala:Q', title="Largura da pétala"),
    alt.Column('especie:N', title='Espécie'),
    alt.Color('especie:N', legend=alt.Legend(title="Espécie"))
).properties(
  width=50,
  height=300
)

comprimento_sepala_chart | largura_sepala_chart | comprimento_petala_chart | largura_pétala_chart

alt.HConcatChart(...)

Apesar da largura da pétala variar menos, é possível constatar que, de fato, o tamanho das pétalas (considerando comprimento e largura) das setosas é menor do que a das outras íris. Já a virgina possui, em média, as maiores pétalas, apesar de possuir observações cujos comprimento e largura se equiparam aos da versicolor.

Também é possível criar uma hipótese sobre a baixa correlação entre o comprimento e a largura das sépalas, mas veremos isso com mais detalhes nas análises bidimensionais.



#### Análise bidimensional

Seria interessante analisar a correlação entre comprimento e largura para as sépalas e pétalas das íris. Inicialmente, vamos exibir isso em um gráfico. Posteriormente analisaremos isso quantitativamente.

In [104]:
comprimento_por_largura_sepala = alt.Chart(iris).mark_point().encode(
    alt.X('largura_sepala:Q', title="Largura da sépala"),
    alt.Y('comprimento_sepala:Q', title="Comprimento da sépala"),
    alt.Color('especie', legend=alt.Legend(title="Espécie"))
)

comprimento_por_largura_petala = alt.Chart(iris).mark_point().encode(
    alt.X('largura_petala:Q', title="Largura da pétala"),
    alt.Y('comprimento_petala:Q', title="Comprimento da pétala"),
    alt.Color('especie', legend=alt.Legend(title="Espécie"))
)

comprimento_por_largura_sepala | comprimento_por_largura_petala

alt.HConcatChart(...)

A correlação entre comprimento e largura da pétala parece ser algo intrínseco das íris, enquanto a correlação para as sépalas não está muito clara e parece ser significante apenas para as setosas.

Vamos, então, quantificar as correlações para as sépalas e pétalas:

In [105]:
print('Correlação entre comprimento e largura das sépalas: ', iris['comprimento_sepala'].corr(iris['largura_sepala']))
print('Correlação entre comprimento e largura das pétalas: ', iris['comprimento_petala'].corr(iris['largura_petala']))

Correlação entre comprimento e largura das sépalas:  -0.11756978413300208
Correlação entre comprimento e largura das pétalas:  0.9628654314027961


A análise quantitativa condiz com a qualitativa.

Agora, vamos ver se a correlação entre comprimento e largura das sépalas ainda é baixa se analisarmos as espécies individualmente:

In [106]:
setosa = iris[iris['especie'] == 'setosa']
print('Correlação entre comprimento e largura das sépalas para as setosas: ', setosa['comprimento_sepala'].corr(setosa['largura_sepala']))

versicolor = iris[iris['especie'] == 'versicolor']
print('Correlação entre comprimento e largura das sépalas para as versicolors: ', versicolor['comprimento_sepala'].corr(versicolor['largura_sepala']))

virginica = iris[iris['especie'] == 'virginica']
print('Correlação entre comprimento e largura das sépalas para as virginicas: ', virginica['comprimento_sepala'].corr(virginica['largura_sepala']))

Correlação entre comprimento e largura das sépalas para as setosas:  0.7425466856651597
Correlação entre comprimento e largura das sépalas para as versicolors:  0.5259107172828243
Correlação entre comprimento e largura das sépalas para as virginicas:  0.4572278163941129


A correlação interna às espécies é maior, com destaque para as setosas. Isso nos leva à conclusão que diferentes espécies têm diferentes proporções de tamanhos de sépalas, enquanto a proporção de tamanho de pétalas parece ser semelhante nas íris.

#### Visualização 1

Vamos fazer uma visualização que permita ver a diferença das características médias entre as espécies:

In [134]:
tamanho_sepala_chart = alt.Chart(iris).mark_bar(color='darkgreen').encode(
    alt.X('especie', title='Espécie'),
    alt.Y('mean(comprimento_sepala):Q', title='Comprimento da sépala'),
    alt.Size('mean(largura_sepala)', scale=alt.Scale(range=[10, 100]), title='Largura da sépala')
).properties(
  width=300,
  height=400
)

tamanho_petala_chart = alt.Chart(iris).mark_bar(color='purple').encode(
    alt.X('especie', title='Espécie'),
    alt.Y('mean(comprimento_petala):Q', title='Comprimento da pétala'),
    alt.Size('mean(largura_petala)', scale=alt.Scale(range=[10, 100]), title='Largura da pétala')
).properties(
  width=300,
  height=400
)

tamanho_sepala_chart | tamanho_petala_chart

alt.HConcatChart(...)

#### Visualização 2

Nessa visualização, gostaria de enxergar as principais características das espécies em um único gráfico. Para isso, utilizo uma nova coluna, chamada `tamanho_petala`, cujo objetivo é quantificar o tamanho de uma pétala através do produto de sua largura pelo seu comprimento. 

In [135]:
iris['tamanho_petala'] = iris['comprimento_petala'] * iris['largura_petala']

iris.head()

comprimento_sepala  largura_sepala  comprimento_petala  largura_petala  \
0                 5.1             3.5                 1.4             0.2   
1                 4.9             3.0                 1.4             0.2   
2                 4.7             3.2                 1.3             0.2   
3                 4.6             3.1                 1.5             0.2   
4                 5.0             3.6                 1.4             0.2   

  especie  tamanho_petala  
0  setosa            0.28  
1  setosa            0.28  
2  setosa            0.26  
3  setosa            0.30  
4  setosa            0.28

In [136]:
tamanho_chart = alt.Chart(iris).mark_circle().encode(
    alt.X('largura_sepala', title='Largura da sépala', scale=alt.Scale(zero=False)),
    alt.Y('comprimento_sepala', title='Comprimento da sépala', scale=alt.Scale(zero=False)),
    alt.Size('tamanho_petala', title='Tamanho da pétala'),
    alt.Color('especie', title="Espécie")
)

tamanho_chart

alt.Chart(...)

### Exemplo 9: Análise do dataset `cars` (Vinicius Prestes)

#### Introdução

Vamos realizar uma análise do dataset `cars` do `vega datasets`.

Agora, vamos carregar o dataset `cars`.

In [107]:
df_cars = data.cars()

O código a seguir simplesmente garante que as colunas numéricas estão com o tipo correto.

In [108]:
df_cars["Weight_in_lbs"] = pd.to_numeric(df_cars["Weight_in_lbs"], errors='coerce')
df_cars["Miles_per_Gallon"] = pd.to_numeric(df_cars["Miles_per_Gallon"], errors='coerce')

#### Exploraçao inicial

Começamos exibindo algumas informações gerais e estatísticas descritivas do dataset.

In [109]:
# Exibir informações gerais do dataset
print("Informações gerais do dataset:")
print(df_cars.info())

# Exibir estatísticas descritivas das colunas numéricas
print("\nEstatísticas descritivas (Média, Mediana, etc.):")
print(df_cars.describe())

Informações gerais do dataset:
<class 'pandas.core.frame.DataFrame'>
RangeIndex: 406 entries, 0 to 405
Data columns (total 9 columns):
 #   Column            Non-Null Count  Dtype         
---  ------            --------------  -----         
 0   Name              406 non-null    object        
 1   Miles_per_Gallon  398 non-null    float64       
 2   Cylinders         406 non-null    int64         
 3   Displacement      406 non-null    float64       
 4   Horsepower        400 non-null    float64       
 5   Weight_in_lbs     406 non-null    int64         
 6   Acceleration      406 non-null    float64       
 7   Year              406 non-null    datetime64[ns]
 8   Origin            406 non-null    object        
dtypes: datetime64[ns](1), float64(4), int64(2), object(2)
memory usage: 28.7+ KB
None

Estatísticas descritivas (Média, Mediana, etc.):
       Miles_per_Gallon   Cylinders  Displacement  Horsepower  Weight_in_lbs  \
count        398.000000  406.000000    406.000000  400

Em seguida, calculamos a média, mediana e a distribuição das variáveis quantitativas (peso e rendimento) bem como a sua distribuição entre os valores assumidos.

In [110]:
# Cálculo de Média
mean_mpg = df_cars["Miles_per_Gallon"].mean()
mean_weight = df_cars["Weight_in_lbs"].mean()
print(f"\nMédia do Consumo de Combustível (mpg): {mean_mpg:.2f}")
print(f"Média do Peso (lbs): {mean_weight:.2f}")

# Cálculo de Mediana
median_mpg = df_cars["Miles_per_Gallon"].median()
median_weight = df_cars["Weight_in_lbs"].median()
print(f"\nMediana do Consumo de Combustível (mpg): {median_mpg:.2f}")
print(f"Mediana do Peso (lbs): {median_weight:.2f}")

# Distribuições de Valores
mpg_distribution = df_cars["Miles_per_Gallon"].value_counts()
weight_distribution = df_cars["Weight_in_lbs"].value_counts()
print("\nDistribuição de Valores (mpg):")
print(mpg_distribution)
print("\nDistribuição de Valores (Peso - lbs):")
print(weight_distribution)


Média do Consumo de Combustível (mpg): 23.51
Média do Peso (lbs): 2979.41

Mediana do Consumo de Combustível (mpg): 23.00
Mediana do Peso (lbs): 2822.50

Distribuição de Valores (mpg):
Miles_per_Gallon
13.0    20
14.0    19
18.0    17
15.0    16
26.0    14
        ..
28.1     1
24.2     1
30.7     1
22.4     1
44.0     1
Name: count, Length: 129, dtype: int64

Distribuição de Valores (Peso - lbs):
Weight_in_lbs
1985    4
2130    4
2125    3
2945    3
2300    3
       ..
4376    1
4382    1
4732    1
2264    1
3433    1
Name: count, Length: 356, dtype: int64


A ser utilizado na primeira visualização, calculamos a frequência de cada valor da variável categórica "Origin".

In [111]:
# Frequência das Categorias em 'Origin'
origin_frequency = df_cars["Origin"].value_counts()
print("\nFrequência das Categorias (Origem):")
print(origin_frequency)


Frequência das Categorias (Origem):
Origin
USA       254
Japan      79
Europe     73
Name: count, dtype: int64


#### Visualização 1: Origem

Veja a seguir um grágráfico de barras mostrado a frequência de cada região (país ou ) na produção dos carros presentes no dataset:

In [112]:
# Criar gráfico de barras da distribuição dos carros por origem
chart_origin = (
    alt.Chart(df_cars)
    .mark_bar()
    .encode(
        x=alt.X("count():Q", title="Número de Carros"),
        y=alt.Y("Origin:N", sort="-x", title="Origem"),
        color=alt.Color("Origin:N", legend=None)
    )
    .properties(title="Distribuição dos Carros por Origem", width=600, height=400)
)

chart_origin.show()

alt.Chart(...)

O gráfico nos permite observar a frequência relativa bem como a quantidade total de regiões produtoras destes carros. Vemos, por exemplo, que apenas dois países e o continente europeu foram envolvidos na produção dos carros, e destes os EUA foram o maior produtor.

#### Visualização 2: Peso x Consumo

O gráfico a seguir é um exemplo de análise bidimensional, correlacionando o peso e o consumo de combustível dos diferentes modelos de automóveis.

In [113]:
# Criar um gráfico de dispersão para analisar a relação entre peso e consumo de combustível
chart_weight_vs_mpg = (
    alt.Chart(df_cars)
    .mark_circle(opacity=0.7)
    .encode(
        x=alt.X("Weight_in_lbs:Q", title="Peso (lbs)"),
        y=alt.Y("Miles_per_Gallon:Q", title="Consumo de Combustível (mpg)"),
        color=alt.Color("Origin:N", title="Origem"),
        tooltip=["Weight_in_lbs", "Miles_per_Gallon", "Origin"]
    )
.properties(title="Relação entre Peso e Consumo de Combustível", width=600, height=400)
)

chart_weight_vs_mpg.show()

alt.Chart(...)

O gráfico acima indica que carros mais pesados tendem a consumir mais combustível (menomenor distância percorrida usando a mesma quantidade de combustível). Podemos ver também que os carros mais pesados (portanto menos econômicos) são produzidos, principalmente, nos EUA, enquanto que os mais leve (portanto mais econômicos) são produzidos, principalmente, no Japão.

### Exemplo 10: (Artur Zaneti)

In [114]:
df = data.airports()
df.head()

iata                  name              city state country   latitude  \
0  00M               Thigpen       Bay Springs    MS     USA  31.953765   
1  00R  Livingston Municipal        Livingston    TX     USA  30.685861   
2  00V           Meadow Lake  Colorado Springs    CO     USA  38.945749   
3  01G          Perry-Warsaw             Perry    NY     USA  42.741347   
4  01J      Hilliard Airpark          Hilliard    FL     USA  30.688012   

    longitude  
0  -89.234505  
1  -95.017928  
2 -104.569893  
3  -78.052081  
4  -81.905944

Para análise básica basta o método `.describe()`

In [115]:
df.describe()

latitude    longitude
count  3376.000000  3376.000000
mean     40.036524   -98.621205
std       8.329559    22.869458
min       7.367222  -176.646031
25%      34.688427  -108.761121
50%      39.434449   -93.599425
75%      43.372612   -84.137519
max      71.285448   145.621384

In [116]:
latitude_hist = alt.Chart(df).mark_bar().encode(
    alt.X('latitude:Q', bin=True),  
    alt.Y('count():Q')  
).properties(
    title="Histograma de Latitude dos Aeroportos"
)

longitude_hist = alt.Chart(df).mark_bar().encode(
    alt.X('longitude:Q', bin=True),
    alt.Y('count():Q')  ).properties(
    title="Histograma de Longitude dos Aeroportos"
)

latitude_hist | longitude_hist

alt.HConcatChart(...)

#### Exemplo 1

A latitude se aproxima de algo "meio normal" mas a longitude não devido a costa. Vamos combinar as informações de latitude e longitude em um gráfico so

In [117]:
scatter_plot = alt.Chart(df).mark_point().encode(
    x='longitude:Q',
    y='latitude:Q'
).properties(
    title="Dispersão de Aeroportos por Latitude e Longitude"
)

scatter_plot


alt.Chart(...)

Está horrivelmente pequeno... Podemos corrigir isso e adicionar uma interatividade mínima

In [118]:
chart = alt.Chart(df).mark_circle(size=50).encode(
    x=alt.X('longitude:Q', title='Longitude'),
    y=alt.Y('latitude:Q', title='Latitude'),
    tooltip=['name:N', 'longitude:Q', 'latitude:Q']
).properties(
    width=800,
    height=600,
    title="Localização dos Aeroportos nos EUA"
)

chart


alt.Chart(...)

#### Exemplo 2

Gostaria de fazer algo usando a coluna "country", mas infelizmente ela não é muito interessante. Basicamente todos os voos são dos EUA (o que justifica o título do gráfico acima)

In [119]:
df["country"].describe()

count     3376
unique       5
top        USA
freq      3372
Name: country, dtype: object

In [120]:
df.head()

iata                  name              city state country   latitude  \
0  00M               Thigpen       Bay Springs    MS     USA  31.953765   
1  00R  Livingston Municipal        Livingston    TX     USA  30.685861   
2  00V           Meadow Lake  Colorado Springs    CO     USA  38.945749   
3  01G          Perry-Warsaw             Perry    NY     USA  42.741347   
4  01J      Hilliard Airpark          Hilliard    FL     USA  30.688012   

    longitude  
0  -89.234505  
1  -95.017928  
2 -104.569893  
3  -78.052081  
4  -81.905944

Bom, mas se todos os voos são dos EUA, vamos tentar olhar quais estados tem mais voos

In [121]:
state_counts = df.groupby('state').size().reset_index(name='flight_count')

chart = alt.Chart(state_counts).mark_bar().encode(
    x=alt.X('state:N', title='Estado'),
    y=alt.Y('flight_count:Q', title='Número de Voos'),
    tooltip=['state:N', 'flight_count:Q']
).properties(
    title='Número de Voos por Estado'
)

chart

alt.Chart(...)

Para facilitar a visualização, vamos ordenar os Estados por quantidade de voos

In [122]:
chart = alt.Chart(state_counts).mark_bar().encode(
    x=alt.X('state:N', title='Estado', sort=alt.EncodingSortField(field='flight_count', op='sum', order='descending')),
    y=alt.Y('flight_count:Q', title='Número de Voos'),
    tooltip=['state:N', 'flight_count:Q']
).properties(
    title='Número de Voos por Estado'
)

chart

alt.Chart(...)

Ficou melhor. Mas podemos tornar o gráfico mais bonito usando cores.

In [123]:
chart = alt.Chart(state_counts).mark_bar(
    color='lightblue',  
    stroke='black',     
    strokeWidth=0.5
).encode(
    x=alt.X('state:N', title='Estado', sort=alt.EncodingSortField(field='flight_count', op='sum', order='descending')),
    y=alt.Y('flight_count:Q', title='Número de Voos'),
    tooltip=['state:N', 'flight_count:Q']
).properties(
    title='Número de Voos por Estado',
    width=800,  
    height=400  
).configure_title(
    fontSize=18,        
    font='Arial',      
    anchor='middle',   
    color='darkblue' 
).configure_axis(
    grid=False,        
    labelFontSize=12,
    titleFontSize=14   
).configure_view(
    strokeWidth=0     
)

chart

alt.Chart(...)

Agora sim 

### Exemplo 11: (Pedro Alberti)

Inicialmente escolhi o dataset disastres e fiz testes iniciais para ver as informações neles

In [124]:
disasters = data.disasters()
disasters.head()

Entity  Year   Deaths
0  All natural disasters  1900  1267360
1  All natural disasters  1901   200018
2  All natural disasters  1902    46037
3  All natural disasters  1903     6506
4  All natural disasters  1905    22758

In [125]:
disasters.Entity.unique()

array(['All natural disasters', 'Drought', 'Earthquake', 'Epidemic',
       'Extreme temperature', 'Extreme weather', 'Flood', 'Landslide',
       'Mass movement (dry)', 'Volcanic activity', 'Wildfire'],
      dtype=object)

Então pensei em olhar de forma geral para os disastres (pelo all natural disasters) ao longo dos anos

In [126]:
disasters_geral = disasters[disasters['Entity'] == 'All natural disasters']
linhas = alt.Chart(disasters_geral).mark_bar().encode(   
    x='Year:T',
    y='Deaths:Q'
)

linhas

alt.Chart(...)

percebe-se inicialmente que recentemente (dos anos 2000 em diante) houve poucas perdas muito grandes como no passado, então farei um recorte temporal e farei algumas análises a partir daí. ( e retirar o all natural disasters por distorcer minhas futuras análises)

In [127]:
disasters_recente = disasters[disasters['Entity'] != 'All natural disasters']
disasters_recente = disasters_recente[disasters_recente['Year'] > 2000]

Então eu tive ideia de 2 visualizações interessantes, 1 com o gráfico mostrando qual foi o disastre natural com maior e outro com a mediana de mortes por ano dos disastres. (caso eu fizesse a média os outliers distorceriam muito)

#### Visualização 1: disastre máximo

A ideia de analisar o disastre com maior fatalidade em cada ano nos traz a informação do impacto de cada disastre natural ao longo do tempo. Pois haverão disastres que não aparecerão em nenhum momento e outras que aparecerão mais de 1 vez, então podemos descobrir qual disastre natural devemos nos precaver mais.

In [128]:
disasters_max_deaths = disasters_recente.loc[disasters_recente.groupby('Year')['Deaths'].idxmax()]

disasters_max_deaths.head(5)

Entity  Year  Deaths
250           Earthquake  2001   21348
320             Epidemic  2002    8762
376  Extreme temperature  2003   74698
253           Earthquake  2004  227290
254           Earthquake  2005   76241

In [129]:
disasters_max_deaths['Year'].describe()

count      17.000000
mean     2009.000000
std         5.049752
min      2001.000000
25%      2005.000000
50%      2009.000000
75%      2013.000000
max      2017.000000
Name: Year, dtype: float64

In [130]:
maximas = alt.Chart(disasters_max_deaths).mark_bar().encode(   
    x='Year:T',
    y='Deaths:Q',
    color='Entity:N',
    tooltip=['Entity:N', 'Deaths:Q']
)

maximas

alt.Chart(...)

Podemos perceber que terremotos e enchentes foram os mais presentes, sendo que enchente parece haver um número mais fixo anual enquanto o terremoto varia muito onde suas altas ultrapassa as demais. Portanto podemos concluir que terremoto é o desastre que mais deveriamos nos precaver.

#### Visualização 2: mediana dos disastres

Desta vez, analiserei como os desastres como um todo impactaram a humanidade nos últimos anos, procurando além de algum padrão uma possível melhora ao longo do tempo.

In [131]:
disasters_median_deaths = disasters_recente.groupby('Year')['Deaths'].median().reset_index()

disasters_median_deaths.head(5)

Year  Deaths
0  2001  1849.0
1  2002  1241.0
2  2003  2285.5
3  2004   284.0
4  2005  1550.0

In [132]:
disasters_median_deaths['Year'].describe()

count      17.000000
mean     2009.000000
std         5.049752
min      2001.000000
25%      2005.000000
50%      2009.000000
75%      2013.000000
max      2017.000000
Name: Year, dtype: float64

In [133]:
median_chart = alt.Chart(disasters_median_deaths).mark_bar().encode(   
    x='Year:T',
    y='Deaths:Q',
    tooltip=['Deaths:Q']
)

median_chart

alt.Chart(...)

Podemos perceber que inicialmente havia uma grande variação entre os anos, enquanto hoje além de estar mais regular percebemos uma queda desde o início.